O Business Case visa entender de que forma as features existentes, e as possiveis novas features a serem criadas para responder melhor o modelo, quanto ao valor de frete que vem sendo empregado, no histórico de vendas e entregas.

Considerando o resultado de nossas métricas de medição quanto ao valor de frete, como propriedade intelectual de posse da OLIST:
 1. Propomos a utilização destas informações como insumo para negociação com o mercado de serviços de transporte.
 2. Indicar as os melhores locais de origem para postagem de um produto especifico.

In [2]:
spark

SparkSession - hive 
 
 
 SparkContext 

 Spark UI 

 
 Version 
 v2.4.5 
 Master 
 local[8] 
 AppName 
 Databricks Shell

In [3]:
display(dbutils.fs.ls('/mnt/datasets/brazilian-ecommerce/'))

path name size dbfs:/mnt/datasets/brazilian-ecommerce/mkt_datasets_arch.png mkt_datasets_arch.png 182541 dbfs:/mnt/datasets/brazilian-ecommerce/olist_closed_deals_dataset.csv olist_closed_deals_dataset.csv 171352 dbfs:/mnt/datasets/brazilian-ecommerce/olist_customers_dataset.csv olist_customers_dataset.csv 9033957 dbfs:/mnt/datasets/brazilian-ecommerce/olist_ecommerce_datasets_arch.png olist_ecommerce_datasets_arch.png 209677 dbfs:/mnt/datasets/brazilian-ecommerce/olist_geolocation_dataset.csv olist_geolocation_dataset.csv 61273883 dbfs:/mnt/datasets/brazilian-ecommerce/olist_marketing_qualified_leads_dataset.csv olist_marketing_qualified_leads_dataset.csv 703836 dbfs:/mnt/datasets/brazilian-ecommerce/olist_order_items_dataset.csv olist_order_items_dataset.csv 15438671 dbfs:/mnt/datasets/brazilian-ecommerce/olist_order_payments_dataset.csv olist_order_payments_dataset.csv 5777138 dbfs:/mnt/datasets/brazilian-ecommerce/olist_order_reviews_dataset.csv olist_order_reviews_dataset.csv 14409007 dbfs:/mnt/datasets/brazilian-ecommerce/olist_orders_dataset.csv olist_orders_dataset.csv 17654914 dbfs:/mnt/datasets/brazilian-ecommerce/olist_products_dataset.csv olist_products_dataset.csv 2379446 dbfs:/mnt/datasets/brazilian-ecommerce/olist_sellers_dataset.csv olist_sellers_dataset.csv 174703 dbfs:/mnt/datasets/brazilian-ecommerce/product_category_name_translation.csv product_category_name_translation.csv 2613

In [4]:
closed_deals = spark.read.csv('/mnt/datasets/brazilian-ecommerce/olist_closed_deals_dataset.csv', header = True, sep = ',', inferSchema=True)
customers = spark.read.csv('/mnt/datasets/brazilian-ecommerce/olist_customers_dataset.csv', header = True, sep = ',', inferSchema=True)
geolocation = spark.read.csv('/mnt/datasets/brazilian-ecommerce/olist_geolocation_dataset.csv', header = True, sep = ',', inferSchema=True)
marketing = spark.read.csv('/mnt/datasets/brazilian-ecommerce/olist_marketing_qualified_leads_dataset.csv', header = True, sep = ',', inferSchema=True)
order_items = spark.read.csv('/mnt/datasets/brazilian-ecommerce/olist_order_items_dataset.csv', header = True, sep = ',', inferSchema=True)
order_payments = spark.read.csv('/mnt/datasets/brazilian-ecommerce/olist_order_payments_dataset.csv', header = True, sep = ',', inferSchema=True)
order_review = spark.read.csv('/mnt/datasets/brazilian-ecommerce/olist_order_reviews_dataset.csv', header = True, sep = ',', inferSchema=True)
orders = spark.read.csv('/mnt/datasets/brazilian-ecommerce/olist_orders_dataset.csv', header = True, sep = ',', inferSchema=True)
products = spark.read.csv('/mnt/datasets/brazilian-ecommerce/olist_products_dataset.csv', header = True, sep = ',', inferSchema=True)
sellers = spark.read.csv('/mnt/datasets/brazilian-ecommerce/olist_sellers_dataset.csv', header = True, sep = ',', inferSchema=True)
product_category = spark.read.csv('/mnt/datasets/brazilian-ecommerce/product_category_name_translation.csv', header = True, sep = ',', inferSchema=True)

In [5]:
from pyspark.sql.functions import isnull, when, count, col

aux = []
for c in order_items.columns:
  aux.append(count(when(isnull(c), c)).alias(c))

display(order_items.select(aux))

order_id order_item_id product_id seller_id shipping_limit_date price freight_value 0 0 0 0 0 0 0

In [6]:
from pyspark.sql.functions import isnull, when, count, col

aux = []
for c in orders.columns:
  aux.append(count(when(isnull(c), c)).alias(c))

display(orders.select(aux))

order_id customer_id order_status order_purchase_timestamp order_approved_at order_delivered_carrier_date order_delivered_customer_date order_estimated_delivery_date 0 0 0 0 160 1783 2965 0

In [7]:
orders = orders.dropDuplicates()

from pyspark.sql.functions import unix_timestamp
orders = orders.withColumn('order_approved_at', unix_timestamp('order_approved_at'))
orders = orders.withColumn('order_delivered_carrier_date', unix_timestamp('order_delivered_carrier_date'))

orders = orders.fillna('NA', subset=['order_approved_at'])
orders = orders.fillna('NA', subset=['order_delivered_carrier_date'])
orders = orders.fillna('NA', subset=['order_delivered_customer_date'])

In [8]:
orders = orders.dropna()
orders.count()

Out[7]: 96461

In [9]:
from pyspark.sql.functions import isnull, when, count, col

aux = []
for c in orders.columns:
  aux.append(count(when(isnull(c), c)).alias(c))

display(orders.select(aux))

order_id customer_id order_status order_purchase_timestamp order_approved_at order_delivered_carrier_date order_delivered_customer_date order_estimated_delivery_date 0 0 0 0 0 0 0 0

In [10]:
from pyspark.sql.functions import isnull, when, count, col

aux = []
for c in order_payments.columns:
  aux.append(count(when(isnull(c), c)).alias(c))

display(order_payments.select(aux))

order_id payment_sequential payment_type payment_installments payment_value 0 0 0 0 0

In [11]:
order_payments = order_payments.dropDuplicates()

installments = order_payments[['payment_installments']].agg({'payment_installments': 'mean'}).collect()[0][0]
order_payments = order_payments.fillna(installments, subset=['payment_installments'])

valor_pagamentos = order_payments[['payment_value']].agg({'payment_value': 'mean'}).collect()[0][0]
order_payments = order_payments.fillna(valor_pagamentos, subset=['payment_value'])

order_payments = order_payments.dropna()
order_payments.count()

Out[10]: 103886

In [12]:
from pyspark.sql.functions import isnull, when, count, col

aux = []
for c in products.columns:
  aux.append(count(when(isnull(c), c)).alias(c))

display(products.select(aux))

product_id product_category_name product_name_lenght product_description_lenght product_photos_qty product_weight_g product_length_cm product_height_cm product_width_cm 0 610 610 610 610 2 2 2 2

In [13]:
lenght = products[['product_name_lenght']].agg({'product_name_lenght': 'mean'}).collect()[0][0]
products = products.fillna(lenght, subset=['product_name_lenght'])

descrip = products[['product_description_lenght']].agg({'product_description_lenght': 'mean'}).collect()[0][0]
products = products.fillna(descrip, subset=['product_description_lenght'])

photo = products[['product_photos_qty']].agg({'product_photos_qty': 'mean'}).collect()[0][0]
products = products.fillna(photo, subset=['product_photos_qty'])

weight = products[['product_weight_g']].agg({'product_weight_g': 'mean'}).collect()[0][0]
products = products.fillna(weight, subset=['product_weight_g'])

lenght_cm = products[['product_length_cm']].agg({'product_length_cm': 'mean'}).collect()[0][0]
products = products.fillna(lenght_cm, subset=['product_length_cm'])

height = products[['product_height_cm']].agg({'product_height_cm': 'mean'}).collect()[0][0]
products = products.fillna(height, subset=['product_height_cm'])

width = products[['product_width_cm']].agg({'product_width_cm': 'mean'}).collect()[0][0]
products = products.fillna(width, subset=['product_width_cm'])

In [14]:
products = products.fillna('NA', subset=['product_category_name'])

In [15]:
products = products.dropDuplicates()
products = products.dropna()
products.count()

Out[14]: 32951

In [16]:
from pyspark.sql.functions import isnull, when, count, col

aux = []
for c in products.columns:
  aux.append(count(when(isnull(c), c)).alias(c))

display(products.select(aux))

product_id product_category_name product_name_lenght product_description_lenght product_photos_qty product_weight_g product_length_cm product_height_cm product_width_cm 0 0 0 0 0 0 0 0 0

In [17]:
from pyspark.sql.functions import isnull, when, count, col

aux = []
for c in customers.columns:
  aux.append(count(when(isnull(c), c)).alias(c))

display(customers.select(aux))

customer_id customer_unique_id customer_zip_code_prefix customer_city customer_state 0 0 0 0 0

In [18]:
from pyspark.sql.functions import isnull, when, count, col

aux = []
for c in sellers.columns:
  aux.append(count(when(isnull(c), c)).alias(c))

display(sellers.select(aux))

seller_id seller_zip_code_prefix seller_city seller_state 0 0 0 0

In [19]:
from pyspark.sql.functions import isnull, when, count, col

aux = []
for c in product_category.columns:
  aux.append(count(when(isnull(c), c)).alias(c))

display(product_category.select(aux))

product_category_name product_category_name_english 0 0

In [20]:
from pyspark.sql.functions import isnull, when, count, col

aux = []
for c in geolocation.columns:
  aux.append(count(when(isnull(c), c)).alias(c))

display(geolocation.select(aux))

geolocation_zip_code_prefix geolocation_lat geolocation_lng geolocation_city geolocation_state 0 0 0 0 0

In [21]:
#if geolocation.count() - geolocation.dropDuplicates().count() > 0:

#Customers
df_Geo_Customers = geolocation
df_Geo_Customers = df_Geo_Customers.repartition(2).cache()
df_Geo_Customers.count()
  
df_Geo_Customers = df_Geo_Customers.fillna('NA', subset=['geolocation_zip_code_prefix'])
df_Geo_Customers = df_Geo_Customers.fillna('NA', subset=['geolocation_lat'])
df_Geo_Customers = df_Geo_Customers.fillna('NA', subset=['geolocation_lng'])
  
df_Geo_Customers = df_Geo_Customers.dropna()
df_Geo_Customers = df_Geo_Customers.dropDuplicates()
df_Geo_Customers = df_Geo_Customers.dropDuplicates(['geolocation_zip_code_prefix'])
  
#Sellers  
df_Geo_Sellers   = geolocation
df_Geo_Sellers = df_Geo_Sellers.repartition(2).cache()
df_Geo_Sellers.count()
  
df_Geo_Sellers = df_Geo_Sellers.fillna('NA', subset=['geolocation_zip_code_prefix'])
df_Geo_Sellers = df_Geo_Sellers.fillna('NA', subset=['geolocation_lat'])
df_Geo_Sellers = df_Geo_Sellers.fillna('NA', subset=['geolocation_lng'])
  
df_Geo_Sellers = df_Geo_Sellers.dropna()
df_Geo_Sellers = df_Geo_Sellers.dropDuplicates()
df_Geo_Sellers = df_Geo_Sellers.dropDuplicates(['geolocation_zip_code_prefix'])

#----------------------------------------------------------------------------------------------------------------
#Customers
df_Geo_Customers = df_Geo_Customers.select('geolocation_zip_code_prefix', 'geolocation_lat', 'geolocation_lng')
df_Geo_Customers = df_Geo_Customers.withColumnRenamed("geolocation_zip_code_prefix", "customer_zip_code_prefix")
df_Geo_Customers = df_Geo_Customers.withColumnRenamed("geolocation_lat"            , "geolocation_lat_customer")
df_Geo_Customers = df_Geo_Customers.withColumnRenamed("geolocation_lng"            , "geolocation_lng_customer")

#Sellers
df_Geo_Sellers = df_Geo_Sellers.select('geolocation_zip_code_prefix', 'geolocation_lat', 'geolocation_lng')
df_Geo_Sellers = df_Geo_Sellers.withColumnRenamed("geolocation_zip_code_prefix", "seller_zip_code_prefix")
df_Geo_Sellers = df_Geo_Sellers.withColumnRenamed("geolocation_lat"            , "geolocation_lat_seller")
df_Geo_Sellers = df_Geo_Sellers.withColumnRenamed("geolocation_lng"            , "geolocation_lng_seller")

display(df_Geo_Sellers)


seller_zip_code_prefix geolocation_lat_seller geolocation_lng_seller 6654 -23.541778046452446 -46.93002461480863 7240 -23.444072161809686 -46.43744029087079 13289 -23.039901147094497 -46.983502576605666 12940 -23.115630732734584 -46.55374249411723 18800 -23.200761987005745 -49.38013003129772 13840 -22.364391224338657 -46.945218901974464 20735 -22.90158024173358 -43.2796028896648 28024 -21.776857352837187 -41.315651564198966 35694 -20.24790925406447 -43.77254802681044 78400 -14.148263999999944 -56.883454999999955 89874 -26.762848632039873 -53.17461320141967 94950 -29.9464588218733 -51.07701750632451 90550 -30.018133875382304 -51.186613038172936 13285 -23.036007913718834 -47.01569708977324 26087 -22.7104362180706 -43.51997330685877 77803 -7.195216930191916 -48.20975100559302 2366 -23.439484341104503 -46.59159597890817 1238 -23.543232348058062 -46.65744549446006 18051 -23.513206389953254 -47.50628567124474 21220 -22.850773467661 -43.31759490580973 31035 -19.89739604766288 -43.91813535137003 71510 -15.7235198731606 -47.889948384124864 70863 -15.752616953163455 -47.88588270143799 62015 -3.6927756155846008 -40.36295575868335 95080 -29.177970599227976 -51.181528516566715 36525 -21.013841999999947 -42.70389199999997 29194 -19.8138679782811 -40.26874801926954 78120 -15.66872461984371 -56.09360000521167 38220 -20.14060703292075 -48.703638230577454 29285 -20.843455784503423 -40.7441120124973 57020 -9.66587479436395 -35.737055435331655 58305 -7.148317184419059 -34.92342508320482 66010 -1.4488003653793808 -48.4982907813145 28664 -22.204999999999927 -42.39805999999993 6620 -23.54587441681086 -46.890995953377214 6397 -23.529142591985227 -46.857849730960375 89056 -26.860078096425028 -49.076764785383624 2866 -23.47104268997064 -46.680753771308176 75705 -18.15167166749383 -47.932905557447086 81900 -25.536530210658427 -49.284382667638056 4101 -23.57408548550999 -46.64029410374809 56640 -8.087217405849508 -37.63787295221013 64590 -7.731631784586615 -40.98752748746071 95940 -29.403260353157698 -51.945492483154595 87120 -23.610883717026965 -52.08142137427222 3175 -23.549946862340555 -46.5844217581222 72820 -16.25130479066359 -47.91072356074285 74820 -16.705172999999945 -49.25079349999996 55155 -8.325129688450756 -36.418169870498836 74775 -16.651543499999992 -49.21113375 75120 -16.344765 -48.966246 5518 -23.586367285042396 -46.72694637108312 40335 -12.952041433185796 -38.49183786194543 59990 -6.19084880766793 -38.22353462770004 14450 -20.309168264656197 -47.59171353075945 26425 -22.685679090461353 -43.60293896049611 9852 -23.74033854958329 -46.603672864439176 23015 -22.905996338882805 -43.53991779892086 63155 -7.28012228207772 -40.45300719195084 45615 -14.954340169122611 -39.30681417068435 65220 -2.9019651945788656 -44.880001076703856 69042 -3.0821471867966417 -60.04891600943507 17420 -22.42071348513878 -49.81930029137705 86082 -23.258463255612035 -51.16528682598529 63106 -7.249890885910003 -39.418795653379064 62680 -3.410174009054141 -39.03208613364559 2122 -23.50935386594724 -46.59097058895492 79220 -21.158504634260083 -55.82622366318382 14570 -20.192231763165623 -47.71419540174471 70355 -15.813481499999998 -47.905794000000014 8592 -23.47075507116463 -46.28983053494729 3918 -23.589680395781627 -46.52101030974089 4935 -23.683851073547252 -46.76601680169083 44022 -12.247885665996126 -38.97355157816301 15790 -20.171836356530793 -50.99946396895056 68610 -1.0236595690611228 -46.637361069578475 19530 -22.0182705 -51.23587725 40386 -12.923033937692637 -38.47945821129166 58835 -6.590710163510188 -37.91394109922627 76110 -16.612203113654758 -50.13347835527228 57380 -10.12661809593617 -36.89832968747444 69048 -3.072010578683137 -60.03434598903573 91785 -30.187861327915748 -51.13588004454206 58665 -6.9412138242413155 -36.628192700275896 63645 -5.803263891023018 -39.246878238119855 57370 -9.965525168829515 -37.00039312888676 55265 -8.538205697021308 -36.7250466146284 2142 -23.511587490420705 -46.57771221593854 53565 -7.901684528449406 -34.905941747994646 8987

In [22]:
from pyspark.sql.functions import isnull, when, count, col

aux = []
for c in df_Geo_Customers.columns:
  aux.append(count(when(isnull(c), c)).alias(c))

display(df_Geo_Customers.select(aux))

customer_zip_code_prefix geolocation_lat_customer geolocation_lng_customer 0 0 0

In [23]:
from pyspark.sql.functions import isnull, when, count, col

aux = []
for c in df_Geo_Sellers.columns:
  aux.append(count(when(isnull(c), c)).alias(c))

display(df_Geo_Sellers.select(aux))

seller_zip_code_prefix geolocation_lat_seller geolocation_lng_seller 0 0 0

In [24]:
#Com estes dados eu crio o codigo do estado para melhorar a acuracia de nosso modelo, podendo utilizar assim o estado como feature na regressao linear
import json
import requests
import copy

from pyspark.sql.functions import *
from pyspark.sql.types import *

def jsonToDataFrame(json, schema=None):
  reader = spark.read
  if schema:
    reader.schema(schema)
  return reader.json(sc.parallelize([json]))

response = requests.get('https://servicodados.ibge.gov.br/api/v1/localidades/estados')

dfUF = jsonToDataFrame(response.json())

display(dfUF)

id nome regiao sigla 11 Rondônia List(1, Norte, N) RO 12 Acre List(1, Norte, N) AC 13 Amazonas List(1, Norte, N) AM 14 Roraima List(1, Norte, N) RR 15 Pará List(1, Norte, N) PA 16 Amapá List(1, Norte, N) AP 17 Tocantins List(1, Norte, N) TO 21 Maranhão List(2, Nordeste, NE) MA 22 Piauí List(2, Nordeste, NE) PI 23 Ceará List(2, Nordeste, NE) CE 24 Rio Grande do Norte List(2, Nordeste, NE) RN 25 Paraíba List(2, Nordeste, NE) PB 26 Pernambuco List(2, Nordeste, NE) PE 27 Alagoas List(2, Nordeste, NE) AL 28 Sergipe List(2, Nordeste, NE) SE 29 Bahia List(2, Nordeste, NE) BA 31 Minas Gerais List(3, Sudeste, SE) MG 32 Espírito Santo List(3, Sudeste, SE) ES 33 Rio de Janeiro List(3, Sudeste, SE) RJ 35 São Paulo List(3, Sudeste, SE) SP 41 Paraná List(4, Sul, S) PR 42 Santa Catarina List(4, Sul, S) SC 43 Rio Grande do Sul List(4, Sul, S) RS 50 Mato Grosso do Sul List(5, Centro-Oeste, CO) MS 51 Mato Grosso List(5, Centro-Oeste, CO) MT 52 Goiás List(5, Centro-Oeste, CO) GO 53 Distrito Federal List(5, Centro-Oeste, CO) DF

In [25]:
#Customers
tabelaUF = dfUF.select('id', 'sigla')
tabelaUF = tabelaUF.withColumnRenamed("id", "codigo_UF_customers")
tabelaUF = tabelaUF.withColumnRenamed("sigla", "customer_state")
tabelaUF_customers = tabelaUF.select('codigo_UF_customers', 'customer_state')

#Sellers
tabelaUF = dfUF.select('id', 'sigla')
tabelaUF = tabelaUF.withColumnRenamed("id", "codigo_UF_sellers")
tabelaUF = tabelaUF.withColumnRenamed("sigla", "seller_state")
tabelaUF_sellers = tabelaUF.select('codigo_UF_sellers', 'seller_state')

In [26]:
#União das bases "orders" com "order_items" utilizando a coluna "order_id".
data_merge = order_items.join(orders, "order_id",how='left')

data_merge = data_merge.repartition(2).cache()
data_merge.count()
data_merge = data_merge.dropDuplicates()

#União das bases "data_merge" com "order_items" utilizando a coluna "order_id".
data_merge = data_merge.join(order_payments, "order_id",how='left')

#União das bases "data_merge" com "products" utilizando a coluna "product_id".
data_merge = data_merge.join(products, "product_id",how='left')

#União das bases "data_merge" com "customers" utilizando a coluna "customer_id".
data_merge = data_merge.join(customers, "customer_id",how='left')

#União das bases "data_merge" com "df_Geo_Customers" utilizando a coluna "customer_zip_code_prefix".
data_merge = data_merge.join(df_Geo_Customers, "customer_zip_code_prefix" ,how='left')

#União das bases "data_merge" com "sellers" utilizando a coluna "seller_id".
data_merge = data_merge.join(sellers, "seller_id" ,how='left')

#União das bases "data_merge" com "df_Geo_Sellers" utilizando a coluna "seller_zip_code_prefix".
data_merge = data_merge.join(df_Geo_Sellers, "seller_zip_code_prefix" ,how='left')

#União das bases "data_merge" com "Tabelas UF" utilizando a coluna "UF".
data_merge = data_merge.join(tabelaUF_customers, "customer_state" ,how='left')

#União das bases "data_merge" com "Tabelas UF" utilizando a coluna "UF".
data_merge = data_merge.join(tabelaUF_sellers, "seller_state" ,how='left')

data_merge = data_merge.repartition(2).cache()
data_merge.count()

display(data_merge)

seller_state customer_state seller_zip_code_prefix seller_id customer_zip_code_prefix customer_id product_id order_id order_item_id shipping_limit_date price freight_value order_status order_purchase_timestamp order_approved_at order_delivered_carrier_date order_delivered_customer_date order_estimated_delivery_date payment_sequential payment_type payment_installments payment_value product_category_name product_name_lenght product_description_lenght product_photos_qty product_weight_g product_length_cm product_height_cm product_width_cm customer_unique_id customer_city geolocation_lat_customer geolocation_lng_customer seller_city geolocation_lat_seller geolocation_lng_seller codigo_UF_customers codigo_UF_sellers SC RS 89224 1a3df491d1c4f1589fc2b934ada68bf2 95045 7a785eeb4a33bdb523fda4d791ce4e0c 2a2d22ae30e026f1893083c8405ca522 1a271fc8bb3a9a776ae5c012bf017ac5 1 2017-05-24T16:45:11.000+0000 134.9 18.19 delivered 2017-05-16T16:35:01.000+0000 1494953111 1495095407 2017-05-30T10:14:34.000+0000 2017-06-09T00:00:00.000+0000 1 credit_card 10 153.09 cama_mesa_banho 60 744 2 8350 50 27 38 5babe7dff334b057190325fe6d7c01c8 caxias do sul -29.123896658685304 -51.16836616682239 joinville -26.260639459893824 -48.80232912031851 43 42 SC RS 88501 eeb6de78f79159600292e314a77cbd18 93700 6c5c5d2e12d767275b124baf4a619093 cc02ea01817f1cb21e6708bc19f1ee20 70dd5f686e8253ebd42e92a545757a86 1 2018-03-12T07:08:29.000+0000 139.0 18.77 delivered 2018-03-05T09:16:43.000+0000 1520320109 1520363624 2018-03-13T21:38:49.000+0000 2018-03-27T00:00:00.000+0000 1 credit_card 5 157.77 industria_comercio_e_negocios 45 704 1 4400 36 12 45 20051fc1229f95f99e0a0b17ce4063a0 campo bom -29.691232419071035 -51.0627944718472 lages -27.813840831525216 -50.33511625506378 43 42 SC RJ 89228 5abb8ea023c77787f2c15da891c8d384 27281 5ccd6e80fc5cdbdf4da5fe51a3d126d0 37244e10d8b612acfba950f0ef0be093 f26d4637c4f560f72ba7feac1675c100 1 2017-12-07T21:17:21.000+0000 399.0 125.78 delivered 2017-12-02T21:01:30.000+0000 1512249441 1513279140 2018-01-17T22:41:45.000+0000 2018-01-03T00:00:00.000+0000 1 credit_card 3 524.78 construcao_ferramentas_construcao 63 1288 5 30000 43 72 43 31127406f4f4cabe57b756540218c700 volta redonda -22.501882645565292 -44.10134295920133 joinville -26.285339342271456 -48.775755957185545 33 42 SC MG 89120 aaed1309374718fdd995ee4c58c9dfcd 38200 bfbf277426eaeed47c31c9cef7fa29d9 794bf14b91dcd92fd3cd35a45d6a83e4 e9740abcb66dbd659a343d7fbf2af04f 1 2017-02-06T09:39:45.000+0000 38.4 17.78 delivered 2017-02-02T09:39:45.000+0000 1486029020 1486035870 2017-02-16T11:38:44.000+0000 2017-03-17T00:00:00.000+0000 1 credit_card 1 56.18 fashion_roupa_masculina 47 316 2 400 16 5 16 511a6ac6371fbba3bad465f3a7b0fc30 frutal -20.020848573248273 -48.91624269316297 timbo -26.792263861667816 -49.27828428616679 31 42 SC null 89460 7008613ea464bad5cb9b83456e1e6a8f null null 3cebb9158a3aa0b3f78ee0f934c9f032 e3c4b2d7022588a02583a79b3f405632 1 2017-03-22T21:14:36.000+0000 59.9 29.35 null null null null null null 1 credit_card 8 89.25 esporte_lazer 41 423 4 1700 28 14 22 null null null null canoinhas -26.18861495746118 -50.37533541603069 null 42 SC MG 88210 c8c1bea22194a4eefa2dc9a9fa89f536 30260 aa54db1f70672e3dd23fe0ce29522fa3 3c3d244942b424b931c33f1ddc122b80 490580980004a090d98d9d45064db2a1 1 2018-06-11T13:50:21.000+0000 186.0 23.01 delivered 2018-06-04T13:52:35.000+0000 1528209109 1528286040 2018-06-14T20:27:27.000+0000 2018-07-16T00:00:00.000+0000 1 boleto 1 209.01 pet_shop 31 612 1 122 17 10 14 20aeef66847d69afc58e891d0560d8b7 belo horizonte -19.928504514570946 -43.905501922009336 porto belo -27.15500703742457 -48.57988625179102 31 42 SC SP 88372 57e632711dec9ec14ca7546769483e7e 15010 d4cc8627da6e9e201f18bfc780b077b1 32272e8a9336baf4548671ac811f4f14 2b44f8afc9f2df6a6090d45db68f9162 1 2018-02-01T16:13:15.000+0000 199.9 17.16 delivered 2018-01-27T16:03:57.000+0000 1517069595 1517247526 2018-02-26T20:15:13.000+0000 2018-03-01T00:00:00.000+0000 1 credit_card 1 217.06 beleza_saude 35 906 2 750 18 

In [27]:
((data_merge.count(), len(data_merge.columns)))
#117604

Out[26]: (117604, 39)

In [28]:
from pyspark.sql.functions import isnull, when, count, col

aux = []
for c in data_merge.columns:
  aux.append(count(when(isnull(c), c)).alias(c))

display(data_merge.select(aux))

seller_state customer_state seller_zip_code_prefix seller_id customer_zip_code_prefix customer_id product_id order_id order_item_id shipping_limit_date price freight_value order_status order_purchase_timestamp order_approved_at order_delivered_carrier_date order_delivered_customer_date order_estimated_delivery_date payment_sequential payment_type payment_installments payment_value product_category_name product_name_lenght product_description_lenght product_photos_qty product_weight_g product_length_cm product_height_cm product_width_cm customer_unique_id customer_city geolocation_lat_customer geolocation_lng_customer seller_city geolocation_lat_seller geolocation_lng_seller codigo_UF_customers codigo_UF_sellers 0 2583 0 0 2583 2583 0 0 0 0 0 0 2583 2583 2583 2583 2583 2583 3 3 3 3 0 0 0 0 0 0 0 0 2583 2583 2881 2881 0 261 261 2583 0

In [29]:

data_merge = data_merge.fillna('NA', subset=['customer_id'])
data_merge = data_merge.fillna('NA', subset=['order_status'])
data_merge = data_merge.fillna('NA', subset=['order_purchase_timestamp'])
data_merge = data_merge.fillna('NA', subset=['order_approved_at'])
data_merge = data_merge.fillna('NA', subset=['order_delivered_carrier_date'])
data_merge = data_merge.fillna('NA', subset=['order_delivered_customer_date'])
data_merge = data_merge.fillna('NA', subset=['order_estimated_delivery_date'])
data_merge = data_merge.fillna('NA', subset=['payment_sequential'])
data_merge = data_merge.fillna('NA', subset=['payment_type'])
data_merge = data_merge.fillna('NA', subset=['product_category_name'])
data_merge = data_merge.fillna('NA', subset=['customer_unique_id'])
data_merge = data_merge.fillna('NA', subset=['customer_zip_code_prefix'])
data_merge = data_merge.fillna('NA', subset=['customer_city'])
data_merge = data_merge.fillna('NA', subset=['customer_state'])


In [30]:
data_merge = data_merge.dropna()
data_merge = data_merge.dropDuplicates()
((data_merge.count(), len(data_merge.columns)))

Out[29]: (114464, 39)

In [31]:
data_merge = data_merge.withColumn("volume", col("product_length_cm") * col("product_height_cm") * col("product_width_cm"))
display(data_merge)

seller_state customer_state seller_zip_code_prefix seller_id customer_zip_code_prefix customer_id product_id order_id order_item_id shipping_limit_date price freight_value order_status order_purchase_timestamp order_approved_at order_delivered_carrier_date order_delivered_customer_date order_estimated_delivery_date payment_sequential payment_type payment_installments payment_value product_category_name product_name_lenght product_description_lenght product_photos_qty product_weight_g product_length_cm product_height_cm product_width_cm customer_unique_id customer_city geolocation_lat_customer geolocation_lng_customer seller_city geolocation_lat_seller geolocation_lng_seller codigo_UF_customers codigo_UF_sellers volume SC SC 88730 1b4c3a6f53068f0b6944d2d005c9fc89 89665 abe7ccf10a2f6af1c6afe529304d54a0 e9a69340883a438c3f91739d14d3a56d 7ff59247bba3cb48642913d4be3bf6ca 1 2017-04-27T15:25:16.000+0000 169.9 17.34 delivered 2017-04-21T15:14:30.000+0000 1492788316 1493027253 2017-05-03T12:27:54.000+0000 2017-05-11T00:00:00.000+0000 1 credit_card 10 187.24 utilidades_domesticas 60 1912 5 3000 33 12 34 c724cdc788aa13dccaf1fd45229b40d6 capinzal -27.34407875722947 -51.60890763491555 sao ludgero -28.333365605408822 -49.18226856361391 42 42 13464 SC RJ 88715 e21a1e8be4715b0fcfd5385643bc49c4 20530 aeb04df5f92479711fd4d147f5a993c3 2aa23c51528b71a1c9f2ce72f4fc9ad8 b3ccff708b4d00e9f5ddbbadfdf427b3 1 2017-07-11T17:41:10.000+0000 31.9 16.79 delivered 2017-07-05T13:45:16.000+0000 1499276470 1499798869 2017-07-19T23:17:56.000+0000 2017-07-31T00:00:00.000+0000 1 credit_card 4 48.69 NA 48 771 2 200 35 4 25 8362d833c1b53d7c08ff61c9d9932225 rio de janeiro -22.943858069680775 -43.254054136072895 jaguaruna -28.622939963827218 -49.019565223979114 33 42 3500 SC BA 88820 fa1a9dec3a9940c072684a46728bf1fc 41338 ba682ab005cd6617c7d3384aabf4a45b 5384f1f55242e82373db2fb7db6047d8 bf4072fdc2122c74befd6df427938cab 1 2018-01-30T15:16:16.000+0000 119.9 20.77 delivered 2018-01-24T14:19:05.000+0000 1516806976 1517358249 2018-02-05T21:18:42.000+0000 2018-02-26T00:00:00.000+0000 1 credit_card 6 235.27 pet_shop 63 1450 3 4050 30 20 40 618ab23cb329ac11c84bc092ddb4bf09 salvador -12.902493530671117 -38.396750427145236 icara -28.679961938970106 -49.31895902654537 29 42 24000 SC DF 89560 7178f9f4dd81dcef02f62acdf8151e01 73105 ec1b208f54047679c3b2c982e22872d0 1a3ed2c0aa5c7beccd817b6b71282e99 188368c093f06fe58e813bd61137b3e1 1 2017-10-23T23:07:07.000+0000 59.9 25.7 delivered 2017-10-13T21:51:40.000+0000 1507932427 1508364473 2017-10-25T22:18:38.000+0000 2017-11-13T00:00:00.000+0000 1 credit_card 5 85.6 eletronicos 54 799 2 600 16 16 11 1f46c0ce030634c7dada0593638d8ba5 brasilia -15.654091048625503 -47.86089188525851 videira -26.987172814468277 -51.17351853835168 53 42 2816 SC MG 89069 b8578d2d823bd8e251f6fdd02b40902d 36087 be8e1d862fb63fadec701434deb1b148 5d1fb1b8ad5adc868c6050e9bddcad27 e06ca49e4892725cc2a5425f4d39048a 1 2018-06-19T16:19:40.000+0000 134.0 22.87 delivered 2018-06-13T15:53:35.000+0000 1528906780 1528980780 2018-06-25T21:42:25.000+0000 2018-07-19T00:00:00.000+0000 1 credit_card 2 156.87 esporte_lazer 53 985 1 800 21 26 21 bf244ab2ac8d4058e8b895effd305a8e juiz de fora -21.70105807660567 -43.42498276977894 blumenau -26.795386959201338 -49.108279924231056 31 42 11466 SC ES 89204 a3a38f4affed601eb87a97788c949667 29285 0597c9c022748f4c23f019f01b8286f4 70d01ae15a5d5ee38388b90c0470d9b0 154f07e395b8990c8aa5a60b0f38fc3e 1 2017-06-06T06:55:24.000+0000 89.99 27.17 delivered 2017-05-29T13:49:46.000+0000 1496213724 1496218435 2017-06-08T13:13:44.000+0000 2017-06-27T00:00:00.000+0000 1 boleto 1 117.16 brinquedos 60 789 2 850 35 6 37 9b364462480c4a10d2c83bcfc2d3dc20 piuma -20.843455784503423 -40.7441120124973 joinville -26.29611808881069 -48.855651113653416 32 42 7770 SC SP 89023 8c16d1f32a54d92897cc437244442e1b 9850 654017a2194ab4ac5d0f58012d5d5a5b afa3bc466a2fbfde2f263266a4dfae3b 371229efe5a72afbbe5fc026b4b8d3a3 1 2018-04-20T08:51:19.000+0000 69.49 13.61 delivered 2018-04-16T08

In [32]:
from pyspark.sql.functions import isnull, when, count, col

aux = []
for c in data_merge.columns:
  aux.append(count(when(isnull(c), c)).alias(c))

display(data_merge.select(aux))

seller_state customer_state seller_zip_code_prefix seller_id customer_zip_code_prefix customer_id product_id order_id order_item_id shipping_limit_date price freight_value order_status order_purchase_timestamp order_approved_at order_delivered_carrier_date order_delivered_customer_date order_estimated_delivery_date payment_sequential payment_type payment_installments payment_value product_category_name product_name_lenght product_description_lenght product_photos_qty product_weight_g product_length_cm product_height_cm product_width_cm customer_unique_id customer_city geolocation_lat_customer geolocation_lng_customer seller_city geolocation_lat_seller geolocation_lng_seller codigo_UF_customers codigo_UF_sellers volume 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0

In [33]:
data_merge.dtypes

Out[32]: [('seller_state', 'string'),
 ('customer_state', 'string'),
 ('seller_zip_code_prefix', 'int'),
 ('seller_id', 'string'),
 ('customer_zip_code_prefix', 'int'),
 ('customer_id', 'string'),
 ('product_id', 'string'),
 ('order_id', 'string'),
 ('order_item_id', 'int'),
 ('shipping_limit_date', 'timestamp'),
 ('price', 'double'),
 ('freight_value', 'double'),
 ('order_status', 'string'),
 ('order_purchase_timestamp', 'timestamp'),
 ('order_approved_at', 'bigint'),
 ('order_delivered_carrier_date', 'bigint'),
 ('order_delivered_customer_date', 'timestamp'),
 ('order_estimated_delivery_date', 'timestamp'),
 ('payment_sequential', 'int'),
 ('payment_type', 'string'),
 ('payment_installments', 'int'),
 ('payment_value', 'double'),
 ('product_category_name', 'string'),
 ('product_name_lenght', 'int'),
 ('product_description_lenght', 'int'),
 ('product_photos_qty', 'int'),
 ('product_weight_g', 'int'),
 ('product_length_cm', 'int'),
 ('product_height_cm', 'int'),
 ('product_width_cm', 'int'),
 ('customer_unique_id', 'string'),
 ('customer_city', 'string'),
 ('geolocation_lat_customer', 'double'),
 ('geolocation_lng_customer', 'double'),
 ('seller_city', 'string'),
 ('geolocation_lat_seller', 'double'),
 ('geolocation_lng_seller', 'double'),
 ('codigo_UF_customers', 'bigint'),
 ('codigo_UF_sellers', 'bigint'),
 ('volume', 'int')]

In [34]:
data_merge = data_merge.repartition(2).cache()
data_merge.count()

Out[33]: 114464

In [35]:
display(data_merge.select('*')\
        .summary('count',
                'min',
                '25%',
                'mean',
                'stddev',
                '50%',
                '75%',
                '85%',
                '95%',
                '99%',
                'max')
       )   
   

summary seller_state customer_state seller_zip_code_prefix seller_id customer_zip_code_prefix customer_id product_id order_id order_item_id price freight_value order_status order_approved_at order_delivered_carrier_date payment_sequential payment_type payment_installments payment_value product_category_name product_name_lenght product_description_lenght product_photos_qty product_weight_g product_length_cm product_height_cm product_width_cm customer_unique_id customer_city geolocation_lat_customer geolocation_lng_customer seller_city geolocation_lat_seller geolocation_lng_seller codigo_UF_customers codigo_UF_sellers volume count 114464 114464 114464 114464 114464 114464 114464 114464 114464 114464 114464 114464 114464 114464 114464 114464 114464 114464 114464 114464 114464 114464 114464 114464 114464 114464 114464 114464 114464 114464 114464 114464 114464 114464 114464 114464 min AM AC 1001 0015a82c2db000af6aaaf3ae2ecb0532 1003 00012a2ce6f8dcda20d059ce98491703 00066f42aeeb9f3007548bb9d3f33c38 00010242fe8c5a6d1ba2dd792cb16214 1 0.85 0.0 canceled 1475574212 1475922841 1 boleto 0 0.0 NA 5 4 1 0 7 2 6 0000366f3b9a7992bf8c76cfdf3221e2 abadia dos dourados -33.69213576773188 -72.66440924999999 abadia de goias -32.07534266241281 -63.89753199919027 11 11 168 25% null null 6440 null 11250 null null null 1 39.9 13.07 null 1505321490 1505498272 1 null 1 60.78 null 43 348 1 300 18 8 15 null null -23.59122894033121 -48.11600404465132 null -23.606031865947237 -48.824481207427674 33 35 2856 mean null null 24461.459078837015 null 35004.60531695555 null null null 1.196655717081353 120.1091003285556 19.988339128459238 null 1.5147902751575603E9 1.515036490839373E9 1.090980570310316 null 2.935446952753704 171.97472454220846 null 48.77820100642997 785.6267298015097 2.201277257478334 2105.8722917249092 30.223502585965893 16.61106548783897 23.049002306402013 null null -21.237722964218417 -46.19903074550951 null -22.797101838275918 -47.23862840288265 34.98000244618395 35.56445694716243 15329.976245806542 stddev null null 27594.367669176685 null 29838.258978199647 null null null 0.7003519267734389 183.2286786535888 15.757562137672544 null 1.3215359132257821E7 1.3189823206153871E7 0.6859407678481656 null 2.771653541235955 266.494868120141 null 9.95117202404227 646.9708508723476 1.7035876735039583 3768.6676973255203 16.118971577333774 13.436378263480682 11.705191462660757 null null 5.56192029756205 4.0433186362933835 null 2.701272644778478 2.34148544028 6.475089327856486 3.5798765692477597 23513.703178298558 50% null null 13660 null 24240 null null null 1 74.9 16.28 null 1516394122 1516741034 1 null 2 108.1 null 51 608 2 700 25 13 20 null null -22.92751716862041 -46.63254194073921 null -23.419823983041162 -46.75356181210684 35 35 6600 75% null null 27930 null 58328 null null null 1 133.0 21.16 null 1525489823 1525780860 1 null 4 188.94 null 57 977 3 1800 38 20 30 null null -20.190602429652138 -43.63316930789028 null -21.76590242683773 -46.522577629753584 35 35 18502 85% null null 65072 null 79010 null null null 1 179.99 26.56 null 1529463301 1529592360 1 null 6 259.84 null 59 1276 4 3600 45 27 35 null null -16.623062999999995 -43.080742626666506 null -21.168954408823375 -46.28172505176295 41 35 29375 95% null null 88350 null 90620 null null null 2 349.9 45.12 null 1533558268 1533738120 1 null 10 510.72 null 60 2110 6 9800 61 45 45 null null -7.986179755112494 -38.505957485429036 null -19.84386009292933 -43.312528246465426 50 42 57760 99% null null 93542 null 97573 null null null 4 889.0 84.45 null 1534825787 1534949520 3 null 10 1202.64 null 63 3362 8 18400 93 65 61 null null -2.5193176360807104 -34.93394133527613 null -11.829237689242529 -38.569608054929475 53 52 112000 max SP TO 99730 ffff564a4f9085cd26170f4732393726 99980 ffffa3172527f765de70084a7e53aae8 fffe9eeff12fcbd74a2f2b007dde0c58 fffe41c64501cc87c801fd61db3f6244 21 6735.0 409.68 delivered 1535555426 1536695308 26 voucher 24 13664.08 utilidades_domesticas 76 3992 20 40425 105 105 118 ffffd2657e2

In [36]:
data_merge = data_merge.dropna()
data_merge.count()

Out[35]: 114464

In [37]:
pandas_data_merge = data_merge.toPandas()

In [38]:
%python
import seaborn as sns
import matplotlib.pyplot as plt
sns.set(rc={'figure.figsize':(20,20)})

#fig, ax = plt.figure()
sns.heatmap(pandas_data_merge.corr(), xticklabels=pandas_data_merge.corr().columns, yticklabels=pandas_data_merge.corr().columns,cmap='RdBu_r',annot=True, cbar=False)
display()

In [39]:
%python
import seaborn as sns
import matplotlib.pyplot as plt
sns.set(rc={'figure.figsize':(20,20)})

#fig, ax = plt.figure()
sns.heatmap(pandas_data_merge.cov(), xticklabels=pandas_data_merge.cov().columns, yticklabels=pandas_data_merge.cov().columns,cmap='RdBu_r',annot=True, cbar=False)
display()

In [40]:
def get_distance(longit_a, latit_a, longit_b, latit_b):
  # Transform to radians
  longit_a, latit_a, longit_b, latit_b = map(radians, [longit_a,  latit_a, longit_b, latit_b])
  dist_longit = longit_b - longit_a
  dist_latit = latit_b - latit_a
  
  # Calculate area
  area = sin(dist_latit/2)**2 + cos(latit_a) * cos(latit_b) * sin(dist_longit/2)**2
  
  # Calculate the central angle
  central_angle = 2 * asin(sqrt(area))
  
  radius = 6371
  # Calculate Distance
  
  distance = central_angle * radius
  
  return abs(round(distance, 2))

#	geolocation_lat_customer	geolocation_lng_customer	seller_city	geolocation_lat_seller	geolocation_lng_seller
data_merge = data_merge.withColumn('distancia_sellers_customers', get_distance('geolocation_lng_seller', 'geolocation_lat_seller', 'geolocation_lng_customer', 'geolocation_lat_customer'))
display(data_merge)

seller_state customer_state seller_zip_code_prefix seller_id customer_zip_code_prefix customer_id product_id order_id order_item_id shipping_limit_date price freight_value order_status order_purchase_timestamp order_approved_at order_delivered_carrier_date order_delivered_customer_date order_estimated_delivery_date payment_sequential payment_type payment_installments payment_value product_category_name product_name_lenght product_description_lenght product_photos_qty product_weight_g product_length_cm product_height_cm product_width_cm customer_unique_id customer_city geolocation_lat_customer geolocation_lng_customer seller_city geolocation_lat_seller geolocation_lng_seller codigo_UF_customers codigo_UF_sellers volume distancia_sellers_customers SP GO 1026 7040e82f899a04d1b434b795a43b4617 74543 f0bf9c83d2300d6c12ce06e16976b267 12f066474dfa3c415c169051c5e1967e 0f7ed09b98de20ce43a56ec76b674951 1 2018-06-25T22:15:58.000+0000 17.9 15.23 delivered 2018-06-19T21:48:53.000+0000 1529446558 1529509320 2018-06-27T17:48:21.000+0000 2018-07-17T00:00:00.000+0000 1 credit_card 3 33.13 telefonia 60 749 3 200 22 8 15 40db5f27c7d20d10678ffef11beaf321 goiania -16.665418951770324 -49.27185810659869 sao paulo -23.539167607276784 -46.63524162031853 52 35 2640 812.32 DF CE 72015 5656537e588803a555b8eb41f07a944b 60810 de2fcb2cca074deebf0c24b2591df6d8 42080692a4543e17940c60a980613abb ebb5b8275a6a365d1243d225386bf299 1 2018-08-14T18:25:16.000+0000 38.89 22.99 delivered 2018-08-09T18:26:03.000+0000 1533925516 1534171980 2018-08-23T21:11:20.000+0000 2018-08-31T00:00:00.000+0000 1 credit_card 1 61.88 eletronicos 27 628 3 200 16 15 15 ed81c5511c2d9be4bdcdad56d26d822a fortaleza -3.769694360811355 -38.48739752622771 brasilia -15.841366153868423 -48.050901858680156 23 53 3600 1701.57 ES SC 29156 001cca7ae9ae17fb1caed9dfb1094831 88745 39fd6d063a9335b98a5045cada7081dc 08574b074924071f4e201e151b152b4e 07dba073c2b18c2c748f28ed51c87ee8 1 2018-02-14T21:28:11.000+0000 101.0 46.01 delivered 2018-02-08T21:14:22.000+0000 1518125291 1518644716 2018-03-09T01:19:23.000+0000 2018-03-13T00:00:00.000+0000 1 credit_card 1 147.01 ferramentas_jardim 36 450 1 9000 42 12 39 89d68ade60d5942d65fa5189c810bdab capivari de baixo -28.45158874983838 -48.95990309203198 cariacica -20.352414794534898 -40.401049001409575 42 32 19656 1248.97 SP SC 14401 7202e2ba20579a9bd1acb29e61fe71f6 88354 d4e7cb01d336245a67f8d43b21c82269 2d0bbec441acd48f8b643a07dd326281 2da6ebf3d4e564ca7ed21893aa78d820 1 2017-10-05T09:28:16.000+0000 174.9 15.97 delivered 2017-09-29T09:18:47.000+0000 1506677296 1506695761 2017-10-10T21:13:39.000+0000 2017-10-26T00:00:00.000+0000 1 credit_card 1 190.87 telefonia 59 1460 2 300 21 11 13 4897a3c64a635a703a71dd2d9189bffa brusque -27.09982962702134 -48.92802784169937 franca -20.53821322305511 -47.390094000000005 42 35 3003 746.17 SP ES 13170 fa1c13f2614d7b5c4749cbc52fecda94 29060 3b1a260815b673185573bec5daed5853 abba23912bdeb1990bd1efa30d888384 9bfc2f3d9f6bdb2f0222e3220a7385f6 1 2017-11-23T18:35:21.000+0000 139.9 14.73 delivered 2017-11-19T18:19:35.000+0000 1511116521 1511392870 2017-11-28T23:27:48.000+0000 2017-12-08T00:00:00.000+0000 1 credit_card 5 154.63 relogios_presentes 56 723 2 200 16 11 11 01d1444a9676bab441621b52773035e9 vitoria -20.281745839027028 -40.29092438008551 sumare -22.823844024822737 -47.26994520496454 32 35 1936 775.01 MG MG 32240 0ebd97a106433a45a4aebe57c1799778 32431 b698dd2f2e777032c13190334b683b0f e8221ea20065e9f3bd2efda98b807cd3 697c79c16c63d9a81a331219b49243e8 1 2018-06-11T08:51:57.000+0000 79.9 7.74 delivered 2018-05-31T13:17:34.000+0000 1527843117 1527862080 2018-06-02T18:08:29.000+0000 2018-06-26T00:00:00.000+0000 1 credit_card 2 87.64 fashion_bolsas_e_acessorios 38 366 3 150 16 6 20 4fbbaf745eef797687df7abd06679f5f ibirite -20.019743595101048 -44.09724133043693 contagem -19.970138983959334 -44.04413131825803 31 31 1920 7.82 SP SP 9400 411f3b52d857390502ee4e4d5ceabc2d 6414 2e1a3155fdbee565b7ad55cb75ce8f78 e8a1dffbef0392ef084cca41655a13d1 6df6c9c9af

In [41]:
pandas_data_merge = data_merge.toPandas()

In [42]:
%python
import seaborn as sns
import matplotlib.pyplot as plt
sns.set(rc={'figure.figsize':(20,20)})

#fig, ax = plt.figure()
sns.heatmap(pandas_data_merge.corr(), xticklabels=pandas_data_merge.corr().columns, yticklabels=pandas_data_merge.corr().columns,cmap='RdBu_r',annot=True, cbar=False)
display()

Verificamos via HeatMap que existe multicolinearidade entre as features order_approved_at e order_delivered_carrier_date, portanto retiramos a featutre order_approved_at do modelo

In [44]:
df = data_merge.select('volume',
                       'distancia_sellers_customers',
                       'order_delivered_carrier_date',
                       'price', 
                       'payment_value',                
                       'product_weight_g', 
                       'codigo_UF_customers',
                       'codigo_UF_sellers',
                       'customer_zip_code_prefix',
                       'geolocation_lat_customer',
                       'geolocation_lng_customer',
                       'seller_zip_code_prefix',
                       'geolocation_lat_seller',
                       'geolocation_lng_seller',
                       'freight_value'
              )  

df = df.repartition(2).cache()
df.count()

display(df)

volume distancia_sellers_customers order_delivered_carrier_date price payment_value product_weight_g codigo_UF_customers codigo_UF_sellers customer_zip_code_prefix geolocation_lat_customer geolocation_lng_customer seller_zip_code_prefix geolocation_lat_seller geolocation_lng_seller freight_value 19800 409.19 1525794900 53.9 53.9 1550 35 35 5074 -23.51963742936693 -46.70513433735358 15025 -20.805236807536087 -49.388535432417434 0.0 1280 831.04 1488365733 20.0 36.05 100 35 43 11075 -23.956979405505155 -46.339395207744246 90010 -30.03362665860703 -51.226860121847736 16.05 2520 1634.75 1523929715 122.99 145.56 650 29 35 48967 -10.332137888567775 -40.153306924122305 9780 -23.71728966749383 -46.53166364458433 22.57 83018 988.53 1496928859 379.99 437.09 9270 29 31 40800 -12.84037566014821 -38.472011979269745 38770 -17.7334098599491 -46.16988120950042 57.1 23920 10.93 1528458420 179.0 192.69 2841 52 52 74890 -16.74774207413882 -49.200307034446965 74645 -16.659819519575453 -49.2461961794748 13.69 1596 590.6 1494510942 281.9 300.31 250 52 31 75180 -16.665088011747898 -48.5979902376516 32604 -19.949831674544328 -44.20067389895847 18.41 2288 341.9 1516404503 99.9 228.8 117 33 35 20220 -22.903192373016367 -43.20251333097695 3804 -23.49807796641469 -46.484685277684804 14.95 7866 422.99 1499430417 59.99 75.16 318 43 41 93025 -29.78075363624141 -51.1588385821945 85501 -26.222809512502536 -52.68371060243072 15.17 8000 347.41 1520976288 28.9 41.69 300 35 35 14600 -20.578204184790337 -47.8669203048702 7160 -23.412087 -46.447888500000005 12.79 640 880.28 1526381040 49.0 64.23 400 53 35 71215 -15.813724999999948 -47.948759999999965 5849 -23.65034498473656 -46.75515749486411 15.23 8000 361.2 1521577130 47.9 123.22 800 35 35 17502 -22.225395441097778 -49.96080297472687 2972 -23.480507026419115 -46.70932575704012 13.71 16200 376.58 1524171564 98.75 114.32 3100 41 35 82515 -25.3868803988379 -49.2286589137217 13920 -22.740512158523465 -46.91388013238744 15.57 816 2.5 1511557942 27.99 35.77 350 35 35 4130 -23.604153600611678 -46.61807401595593 4160 -23.625863266720533 -46.61180698251485 7.78 5832 1411.45 1531232520 89.49 52.05 200 29 35 45400 -13.375145058828178 -39.07591102353127 11701 -24.003710669016144 -46.41645739819209 22.56 23625 298.48 1502722680 69.9 165.46 800 35 35 2205 -23.486559233971946 -46.592233768942236 14940 -21.76590242683773 -48.824481207427674 12.83 32560 403.66 1505169172 59.9 146.68 1750 35 35 5174 -23.482167401610013 -46.74091120760001 15025 -20.805236807536087 -49.388535432417434 13.44 15000 420.41 1528182120 55.0 68.75 800 35 35 15075 -20.818102609080245 -49.355290357453114 4782 -23.693964632523542 -46.70285535082804 13.75 4125 509.96 1499972268 35.9 53.5 950 31 35 30230 -19.920877042527124 -43.87805189454315 13324 -23.206566074093192 -47.31913346585179 17.6 8892 1155.79 1502137967 144.9 172.45 600 29 35 47810 -12.136526695228756 -45.00580568662077 27277 -22.496746075768943 -44.124033939494495 27.55 936 650.28 1510178957 29.99 45.09 217 42 35 88812 -28.788293016407128 -49.36505869094748 3569 -23.54026727338563 -46.48834801082004 15.1 3960 665.61 1489391672 187.9 209.3 4800 31 35 30590 -19.96093225867046 -43.99539464556528 17515 -22.209328692552198 -49.942004869044496 21.4 640 616.22 1524825660 49.0 163.66 400 31 35 36900 -20.255964232052968 -42.03083319337746 5849 -23.65034498473656 -46.75515749486411 18.33 34650 887.26 1532507520 195.0 262.9 9350 33 42 22770 -22.940694407726852 -43.35865638022974 88504 -27.82453022231519 -50.347390453228726 67.9 4800 279.58 1501164690 18.9 30.75 300 35 35 6624 -23.55241510253078 -46.90714366200811 14940 -21.76590242683773 -48.824481207427674 11.85 4352 459.95 1532078880 27.49 45.78 50 31 35 36572 -20.75784881275068 -42.88933473704877 12940 -23.115630732734584 -46.55374249411723 18.29 6318 823.3 1524075124 119.99 135.71 250 53 31 71931 -15.83612305024187 -48.04018517722967 36010 -21.760592332506164 -43.346038803364266 15.72 10773 19.7 1520335816 419.9 430.09 1167 35 35 13140 -22.77913481181838 

In [45]:
df = df.dropDuplicates()
df.count()

Out[43]: 103268

In [46]:
df.dtypes

Out[44]: [('volume', 'int'),
 ('distancia_sellers_customers', 'double'),
 ('order_delivered_carrier_date', 'bigint'),
 ('price', 'double'),
 ('payment_value', 'double'),
 ('product_weight_g', 'int'),
 ('codigo_UF_customers', 'bigint'),
 ('codigo_UF_sellers', 'bigint'),
 ('customer_zip_code_prefix', 'int'),
 ('geolocation_lat_customer', 'double'),
 ('geolocation_lng_customer', 'double'),
 ('seller_zip_code_prefix', 'int'),
 ('geolocation_lat_seller', 'double'),
 ('geolocation_lng_seller', 'double'),
 ('freight_value', 'double')]

In [47]:
display(data_merge.select('order_status').groupBy('order_status').count())

order_status count canceled 7 delivered 114457

In [48]:
data_merge = data_merge.where(data_merge['order_status'] == 'delivered')
data_merge.count()

Out[46]: 114457

In [49]:
display(data_merge.select('*').orderBy('customer_state', ascending=False, ))

seller_state customer_state seller_zip_code_prefix seller_id customer_zip_code_prefix customer_id product_id order_id order_item_id shipping_limit_date price freight_value order_status order_purchase_timestamp order_approved_at order_delivered_carrier_date order_delivered_customer_date order_estimated_delivery_date payment_sequential payment_type payment_installments payment_value product_category_name product_name_lenght product_description_lenght product_photos_qty product_weight_g product_length_cm product_height_cm product_width_cm customer_unique_id customer_city geolocation_lat_customer geolocation_lng_customer seller_city geolocation_lat_seller geolocation_lng_seller codigo_UF_customers codigo_UF_sellers volume distancia_sellers_customers RJ TO 26551 c35672b10ad50968f567ea3f4b91e877 77018 c99c8103d1af91b19f82cec25c9a348b 51d646c5c93e0f1de543528d0e24eadc 9d4c848f67a05d1b2d6f9f9fe1c932c8 1 2018-08-01T10:50:12.000+0000 69.99 22.77 delivered 2018-07-27T13:03:40.000+0000 1532775012 1532953800 2018-08-06T17:59:46.000+0000 2018-08-22T00:00:00.000+0000 1 debit_card 1 92.76 beleza_saude 46 1305 1 1400 27 10 17 c7ef94646db3745837b7449af9f3fe5b palmas -10.245064403411298 -48.345523202361676 mesquita -22.78552489490268 -43.42403305376965 17 33 4590 1489.4 GO TO 75650 65b081a070633e057c462abdd6fb9dd8 77006 5ffcd627277b345a8ea9ec164c94c82b cc1b5f3a64b4f452bdf5473f10dc6aaf 6de969bc5e6479d498ca1f31da9b347a 1 2018-04-11T22:55:21.000+0000 45.0 18.23 delivered 2018-04-06T22:41:16.000+0000 1523055321 1523302006 2018-04-17T19:43:45.000+0000 2018-05-03T00:00:00.000+0000 1 credit_card 1 63.23 perfumaria 28 318 2 388 19 12 14 390fe700700a68c98d9efecaf2cc6d91 palmas -10.176993077193695 -48.332088997185515 morrinhos -17.724608450664327 -49.1111939482517 17 52 3192 843.45 SP TO 3237 b76dba6c951ab00dc4edf0a1aa88037e 77665 9fcfab0ef8326a8e5d435076772086c4 913580fde3e72c3b3e4ce0b79963bee6 af8822dc30a41edce5b644f195e3f269 1 2017-02-17T15:55:09.000+0000 10.99 17.78 delivered 2017-02-13T15:55:09.000+0000 1487001923 1487070339 2017-03-09T09:37:44.000+0000 2017-03-20T00:00:00.000+0000 1 credit_card 1 28.77 telefonia_fixa 53 318 4 100 16 5 13 e10142a5628ef46a46277528061e78a6 barrolandia -9.834764368654687 -48.723527956708296 sao paulo -23.595301571469772 -46.55179691548847 17 35 1040 1547.38 SP TO 9628 f7ba60f8c3f99e7ee4042fdef03b70c4 77015 1ee4ffefe39f642db2fc25a2095b598a bb50f2e236e5eea0100680137654686c 7feb0201e5b3afef04792d32b483cc17 1 2017-10-04T14:28:20.000+0000 325.0 19.55 delivered 2017-09-28T14:14:37.000+0000 1506608900 1506705542 2017-10-23T16:32:37.000+0000 2017-10-25T00:00:00.000+0000 1 credit_card 6 344.55 beleza_saude 60 2644 6 400 34 4 22 2b396aaaa02866a6942f7d6e1c3bf654 palmas -10.209317161601478 -48.338457029023694 sao bernardo do campo -23.660199240088787 -46.56568437731553 17 35 2992 1507.44 SP TO 13347 8c5e007d7bd5693fa1386ffefbc99f6c 77016 82cc4a44845768c5fe11c6580f2b48b3 7c1ac37ea884ec9c46ebf155ffc53d50 5dba08d21f1386085c1bdd47548f34a4 1 2018-07-04T15:51:46.000+0000 40.16 19.19 delivered 2018-06-28T15:31:49.000+0000 1530201106 1530512460 2018-07-10T12:08:53.000+0000 2018-07-26T00:00:00.000+0000 1 credit_card 4 356.1 beleza_saude 44 274 2 250 22 12 17 334054ef166f76dd657564ac53c858fc palmas -10.220253655906816 -48.33809030397393 indaiatuba -23.13879211792097 -47.233449815836195 17 35 4488 1441.26 DF TO 70645 768de2a4fc06aacecb9a586ccc30746a 77600 b8b9cd163d230f13301c8ece6f71eb58 aadae4da0b9feede5777009c5e1497d1 666a6228ea2363c308924bc929101d7f 1 2017-08-30T14:26:49.000+0000 32.9 15.1 delivered 2017-08-22T13:18:25.000+0000 1503412009 1503499527 2017-09-01T18:22:35.000+0000 2017-09-18T00:00:00.000+0000 1 credit_card 2 48.0 livros_interesse_geral 60 2671 4 600 20 22 14 b5912b610fb1cf78a1b48c3a151d9311 paraiso do tocantins -10.177203655783707 -48.892706420631 brasilia -15.782105504364816 -47.93233498642118 17 53 6160 631.86 SP TO 9163 bc47d5d1490df2b36add65d733eafaba 77500 681a0a16e33799607c5f5be2c0b7195a c1cf8f51eac90b1ff478250b3d35c37b 

In [50]:
#Verificamos aqui que há muitos outiliers de valor maiores que 40, portanto para este caso especifico nos focaremos nos fretes com valores menores que 
display(data_merge.select('freight_value'))

freight_value 15.23 22.99 46.01 15.97 14.73 7.74 8.3 12.79 17.73 23.99 38.46 10.86 7.39 16.14 15.1 9.34 19.3 18.43 19.32 22.88 27.98 15.33 18.65 20.49 15.37 11.85 7.87 17.93 23.04 21.2 24.84 26.67 13.08 15.1 7.46 16.85 14.09 11.99 18.02 163.37 18.1 13.26 27.02 7.71 25.18 16.74 15.56 7.39 11.85 23.19 38.11 15.52 13.0 21.02 12.69 18.5 12.4 55.93 29.73 11.15 16.42 7.9 22.06 18.37 16.79 19.87 18.37 32.34 101.57 19.92 21.15 14.1 6.34 11.85 22.77 37.16 54.33 25.63 13.15 11.85 9.51 11.82 38.39 53.05 22.81 11.85 20.03 98.15 15.1 16.11 15.57 15.1 17.78 33.08 28.42 7.39 25.68 22.14 14.02 8.58 22.93 13.85 18.19 7.39 21.18 19.32 16.86 15.6 12.9 9.37 14.15 36.75 15.1 15.27 16.07 16.57 14.1 14.1 50.85 19.23 16.12 18.24 14.34 16.69 11.85 17.09 38.03 21.79 14.1 21.54 11.85 14.1 15.98 15.1 84.39 7.39 18.23 14.52 25.63 14.1 15.33 7.39 33.71 13.31 27.14 27.17 15.1 15.0 14.43 23.33 12.59 38.8 12.99 18.23 8.72 9.12 18.0 27.25 13.58 14.52 13.7 8.29 18.09 9.1 15.23 14.1 22.0 23.44 24.84 21.47 62.35 9.27 13.61 14.28 13.44 35.08 25.95 29.1 17.6 41.68 14.59 12.8 14.24 25.13 12.48 17.67 22.98 15.95 15.3 14.49 16.18 12.35 14.25 10.96 16.97 17.94 15.35 9.16 11.96 22.06 28.89 18.17 13.92 12.92 16.86 21.18 20.47 14.52 17.6 15.1 14.14 19.94 18.23 18.47 14.24 26.89 26.63 18.0 24.54 22.93 23.11 13.0 5.91 16.6 16.79 25.7 17.41 18.95 10.04 17.67 17.29 12.69 13.08 59.91 8.88 20.81 30.06 13.86 7.39 12.69 18.27 17.85 8.03 13.5 15.1 8.82 11.85 16.32 26.86 9.31 14.42 16.3 7.78 43.68 15.44 12.43 23.29 8.82 14.52 25.29 17.8 22.96 15.37 16.02 8.29 15.1 12.79 29.44 29.98 28.63 19.83 19.59 18.5 14.6 18.23 7.78 12.84 15.57 15.18 31.8 12.48 16.11 15.11 8.37 19.32 22.65 52.11 12.79 14.23 17.29 17.6 12.83 11.85 17.54 21.88 20.82 17.83 15.26 28.12 11.03 13.36 15.1 12.49 14.1 15.1 14.52 9.27 16.87 20.93 8.72 7.39 16.0 23.6 18.5 17.74 12.02 22.93 13.79 20.89 17.8 15.88 18.33 21.3 15.23 7.39 18.23 8.29 13.14 16.96 31.94 15.68 12.02 16.92 22.93 17.78 17.43 15.11 22.84 14.31 39.16 13.44 16.22 13.01 21.29 12.79 23.7 14.33 17.21 8.98 18.3 98.81 16.32 22.57 76.44 23.39 64.67 19.59 23.34 8.84 13.71 15.27 7.39 12.69 12.76 26.61 12.32 8.72 38.37 21.22 13.11 38.37 16.6 30.43 21.6 18.23 56.9 9.41 13.57 35.67 35.82 18.23 16.1 18.23 35.43 17.12 33.21 11.88 16.6 13.57 11.85 12.88 6.78 17.63 19.71 16.21 13.44 12.93 7.87 38.84 17.6 16.32 27.11 15.1 15.1 19.36 7.78 16.41 18.24 15.85 9.7 27.64 9.01 16.37 16.86 8.63 15.31 15.23 15.1 8.88 59.62 20.4 18.23 9.34 15.85 11.85 62.17 25.03 15.1 20.7 14.42 16.55 16.11 23.01 16.7 13.41 15.23 16.79 15.3 8.91 18.4 15.89 20.01 25.08 9.44 15.1 15.36 15.41 20.15 18.66 7.78 20.8 47.82 8.03 15.79 7.39 19.65 11.85 7.39 15.1 38.79 16.68 17.19 12.48 15.79 15.25 20.26 61.04 18.29 12.15 11.15 43.47 16.79 14.0 16.43 15.23 18.31 9.37 13.37 15.1 16.79 16.26 13.47 16.16 15.79 17.03 23.17 8.53 16.05 18.5 7.43 37.04 12.74 15.23 22.66 37.92 17.83 25.18 15.51 16.33 19.19 18.58 18.23 15.28 21.35 25.83 14.91 16.79 17.92 27.13 13.16 14.04 11.85 14.65 14.1 20.54 19.6 27.75 7.39 7.39 11.79 13.51 18.46 11.85 56.56 15.83 9.87 17.34 8.88 13.18 18.66 17.63 7.64 19.59 9.48 9.24 17.37 18.28 20.84 8.72 25.63 4.44 12.79 15.34 19.63 70.73 16.28 14.1 19.63 17.63 14.11 11.88 12.71 9.33 8.27 9.05 14.36 23.06 17.88 17.92 15.1 25.84 7.74 24.59 16.79 14.1 13.74 15.27 23.35 30.19 20.08 19.16 18.93 12.99 16.18 9.34 104.0 7.78 9.03 16.56 19.6 7.78 18.5 19.4 22.88 15.1 8.11 11.67 15.36 22.06 15.65 17.63 12.25 29.44 17.92 15.38 15.9 27.44 15.43 23.9 15.56 9.56 15.45 18.1 12.93 9.94 15.53 43.4 10.12 17.81 38.99 8.73 21.9 14.72 36.29 19.4 12.54 16.74 18.31 21.22 14.03 20.6 30.64 17.53 22.64 24.35 19.11 11.39 12.69 12.79 13.07 17.16 25.02 11.15 11.85 14.2 6.34 15.5 16.77 27.39 13.78 12.79 84.59 16.05 11.85 7.95 13.83 12.8 18.2 17.74 15.14 7.78 22.15 9.34 9.48 42.65 13.37 21.3 15.1 16.11 10.07 15.1 18.29 8.04 14.59 8.53 26.27 24.41 21.88 12.05 17.21 17.6 14.09 12.48 13.79 15.95 15.1 11.85 15.83 14.8 7.78 13.43 7.78 13.78 37.55 8.88 24.97 26.9 8.96 8.91 8.09 15.23 12.79 11.73 15.11 19.13 20.5 21.09 15.1 1

In [51]:
display(data_merge.select('freight_value'))

freight_value 15.23 22.99 46.01 15.97 14.73 7.74 8.3 12.79 17.73 23.99 38.46 10.86 7.39 16.14 15.1 9.34 19.3 18.43 19.32 22.88 27.98 15.33 18.65 20.49 15.37 11.85 7.87 17.93 23.04 21.2 24.84 26.67 13.08 15.1 7.46 16.85 14.09 11.99 18.02 163.37 18.1 13.26 27.02 7.71 25.18 16.74 15.56 7.39 11.85 23.19 38.11 15.52 13.0 21.02 12.69 18.5 12.4 55.93 29.73 11.15 16.42 7.9 22.06 18.37 16.79 19.87 18.37 32.34 101.57 19.92 21.15 14.1 6.34 11.85 22.77 37.16 54.33 25.63 13.15 11.85 9.51 11.82 38.39 53.05 22.81 11.85 20.03 98.15 15.1 16.11 15.57 15.1 17.78 33.08 28.42 7.39 25.68 22.14 14.02 8.58 22.93 13.85 18.19 7.39 21.18 19.32 16.86 15.6 12.9 9.37 14.15 36.75 15.1 15.27 16.07 16.57 14.1 14.1 50.85 19.23 16.12 18.24 14.34 16.69 11.85 17.09 38.03 21.79 14.1 21.54 11.85 14.1 15.98 15.1 84.39 7.39 18.23 14.52 25.63 14.1 15.33 7.39 33.71 13.31 27.14 27.17 15.1 15.0 14.43 23.33 12.59 38.8 12.99 18.23 8.72 9.12 18.0 27.25 13.58 14.52 13.7 8.29 18.09 9.1 15.23 14.1 22.0 23.44 24.84 21.47 62.35 9.27 13.61 14.28 13.44 35.08 25.95 29.1 17.6 41.68 14.59 12.8 14.24 25.13 12.48 17.67 22.98 15.95 15.3 14.49 16.18 12.35 14.25 10.96 16.97 17.94 15.35 9.16 11.96 22.06 28.89 18.17 13.92 12.92 16.86 21.18 20.47 14.52 17.6 15.1 14.14 19.94 18.23 18.47 14.24 26.89 26.63 18.0 24.54 22.93 23.11 13.0 5.91 16.6 16.79 25.7 17.41 18.95 10.04 17.67 17.29 12.69 13.08 59.91 8.88 20.81 30.06 13.86 7.39 12.69 18.27 17.85 8.03 13.5 15.1 8.82 11.85 16.32 26.86 9.31 14.42 16.3 7.78 43.68 15.44 12.43 23.29 8.82 14.52 25.29 17.8 22.96 15.37 16.02 8.29 15.1 12.79 29.44 29.98 28.63 19.83 19.59 18.5 14.6 18.23 7.78 12.84 15.57 15.18 31.8 12.48 16.11 15.11 8.37 19.32 22.65 52.11 12.79 14.23 17.29 17.6 12.83 11.85 17.54 21.88 20.82 17.83 15.26 28.12 11.03 13.36 15.1 12.49 14.1 15.1 14.52 9.27 16.87 20.93 8.72 7.39 16.0 23.6 18.5 17.74 12.02 22.93 13.79 20.89 17.8 15.88 18.33 21.3 15.23 7.39 18.23 8.29 13.14 16.96 31.94 15.68 12.02 16.92 22.93 17.78 17.43 15.11 22.84 14.31 39.16 13.44 16.22 13.01 21.29 12.79 23.7 14.33 17.21 8.98 18.3 98.81 16.32 22.57 76.44 23.39 64.67 19.59 23.34 8.84 13.71 15.27 7.39 12.69 12.76 26.61 12.32 8.72 38.37 21.22 13.11 38.37 16.6 30.43 21.6 18.23 56.9 9.41 13.57 35.67 35.82 18.23 16.1 18.23 35.43 17.12 33.21 11.88 16.6 13.57 11.85 12.88 6.78 17.63 19.71 16.21 13.44 12.93 7.87 38.84 17.6 16.32 27.11 15.1 15.1 19.36 7.78 16.41 18.24 15.85 9.7 27.64 9.01 16.37 16.86 8.63 15.31 15.23 15.1 8.88 59.62 20.4 18.23 9.34 15.85 11.85 62.17 25.03 15.1 20.7 14.42 16.55 16.11 23.01 16.7 13.41 15.23 16.79 15.3 8.91 18.4 15.89 20.01 25.08 9.44 15.1 15.36 15.41 20.15 18.66 7.78 20.8 47.82 8.03 15.79 7.39 19.65 11.85 7.39 15.1 38.79 16.68 17.19 12.48 15.79 15.25 20.26 61.04 18.29 12.15 11.15 43.47 16.79 14.0 16.43 15.23 18.31 9.37 13.37 15.1 16.79 16.26 13.47 16.16 15.79 17.03 23.17 8.53 16.05 18.5 7.43 37.04 12.74 15.23 22.66 37.92 17.83 25.18 15.51 16.33 19.19 18.58 18.23 15.28 21.35 25.83 14.91 16.79 17.92 27.13 13.16 14.04 11.85 14.65 14.1 20.54 19.6 27.75 7.39 7.39 11.79 13.51 18.46 11.85 56.56 15.83 9.87 17.34 8.88 13.18 18.66 17.63 7.64 19.59 9.48 9.24 17.37 18.28 20.84 8.72 25.63 4.44 12.79 15.34 19.63 70.73 16.28 14.1 19.63 17.63 14.11 11.88 12.71 9.33 8.27 9.05 14.36 23.06 17.88 17.92 15.1 25.84 7.74 24.59 16.79 14.1 13.74 15.27 23.35 30.19 20.08 19.16 18.93 12.99 16.18 9.34 104.0 7.78 9.03 16.56 19.6 7.78 18.5 19.4 22.88 15.1 8.11 11.67 15.36 22.06 15.65 17.63 12.25 29.44 17.92 15.38 15.9 27.44 15.43 23.9 15.56 9.56 15.45 18.1 12.93 9.94 15.53 43.4 10.12 17.81 38.99 8.73 21.9 14.72 36.29 19.4 12.54 16.74 18.31 21.22 14.03 20.6 30.64 17.53 22.64 24.35 19.11 11.39 12.69 12.79 13.07 17.16 25.02 11.15 11.85 14.2 6.34 15.5 16.77 27.39 13.78 12.79 84.59 16.05 11.85 7.95 13.83 12.8 18.2 17.74 15.14 7.78 22.15 9.34 9.48 42.65 13.37 21.3 15.1 16.11 10.07 15.1 18.29 8.04 14.59 8.53 26.27 24.41 21.88 12.05 17.21 17.6 14.09 12.48 13.79 15.95 15.1 11.85 15.83 14.8 7.78 13.43 7.78 13.78 37.55 8.88 24.97 26.9 8.96 8.91 8.09 15.23 12.79 11.73 15.11 19.13 20.5 21.09 15.1 1

In [52]:
res_estat = data_merge.select('freight_value').where(data_merge['freight_value'] >= 5)\
        .summary('count',
                'min',
                '25%',
                'mean',
                'stddev',
                '50%',
                '75%',
                '85%',
                '90%',
                '95%',
                '99%',
                'max')

#No intuito de eliminar os outiliers que neste modelo em especifico, são um dos maiores detratores dos melhores resultado de previsao do modelo
#foram selecionados 85% de toda a base de dados, que são os valores de frete entre R$ 5,00 e 26.72   

#nMin = res_estat.select(res_estat['freight_value']).where(res_estat['summary'] == 'min' ).collect()[0]['freight_value']
nMin = 5
n85 = res_estat.select(res_estat['freight_value']).where(res_estat['summary'] == '85%' ).collect()[0]['freight_value']
#nMaxM = res_estat.select(res_estat['freight_value']).where(res_estat['summary'] == 'max' ).collect()[0]['freight_value']

nMax = n85
#nMax = nMaxM

print('Valor minimo de frete definido: ')
print(nMin)
print('Valor máximo de frete definido: ')
print(nMax)
          
display(res_estat)      

summary freight_value count 113199 min 5.0 25% 13.25 mean 20.190677214462646 stddev 15.726549971315679 50% 16.35 75% 21.25 85% 26.72 90% 34.15 95% 45.29 99% 84.6 max 409.68

In [53]:
data_merge_total = df

data_merge_total = data_merge_total.repartition(2).cache()
data_merge_total.count()

data_merge_Slice = df.where((df['freight_value'] >= nMin) & (df['freight_value'] <= nMax))

data_merge_Slice = data_merge_Slice.repartition(2).cache()
data_merge_Slice.count()

#Antes verifico a quantidade registros que serão descartados
print(data_merge_total.count() - data_merge_Slice.count())

df = data_merge_Slice


16527

In [54]:
#Verificamos aqui que há muitos outiliers de valor maiores que 40, portanto para este caso especifico nos focaremos nos fretes com valores menores que 
display(data_merge_Slice.select('freight_value'))

freight_value 13.25 18.12 14.17 17.67 25.61 9.34 15.34 19.5 22.77 14.62 17.05 7.45 16.25 8.29 16.11 22.14 12.69 12.79 13.43 7.57 7.8 11.86 23.93 17.06 12.69 19.05 12.69 9.94 18.05 26.43 18.95 17.11 8.29 13.96 17.67 16.88 12.86 8.72 7.78 18.93 16.79 16.69 16.99 17.95 13.37 17.67 23.28 17.0 15.1 15.1 16.79 10.55 12.78 18.43 16.45 18.3 14.42 12.21 18.54 15.23 11.98 9.13 14.29 8.48 14.09 14.1 21.64 8.27 18.49 10.96 15.25 9.6 8.57 15.1 20.26 7.78 17.63 7.39 22.34 11.53 13.02 16.34 12.69 19.29 19.04 15.65 17.46 14.1 13.65 9.23 16.52 22.56 17.95 12.49 12.48 12.76 20.23 8.29 11.85 9.53 19.05 7.87 7.65 22.59 14.32 10.96 15.24 14.52 17.64 7.39 13.11 15.23 21.6 10.83 15.43 17.26 18.23 9.34 19.53 14.3 18.59 22.85 15.59 16.14 15.1 15.79 20.28 20.98 11.74 16.18 7.67 18.42 12.04 18.61 16.19 7.44 14.0 18.37 13.83 15.1 13.39 18.16 13.72 8.3 8.72 15.1 7.39 7.77 12.69 7.75 18.33 14.04 15.23 13.71 6.0 22.06 14.1 16.11 15.23 8.82 16.94 15.23 8.27 7.39 18.08 18.63 12.71 12.43 24.73 16.79 24.55 17.78 18.53 14.1 15.1 23.07 13.25 7.48 16.11 14.79 19.18 16.73 18.23 14.35 16.2 15.1 15.46 23.19 24.93 18.23 12.13 11.85 12.48 15.76 17.67 13.38 7.71 17.63 16.11 15.1 19.38 16.93 11.31 18.26 19.97 8.88 15.46 16.84 15.14 15.07 16.11 18.59 12.55 22.38 24.14 14.13 11.81 24.32 17.83 18.29 18.23 14.77 18.71 8.88 25.63 23.62 21.73 12.89 18.65 13.08 18.44 23.7 15.1 20.52 22.41 9.36 15.23 19.06 19.32 24.12 24.61 7.89 16.61 20.59 15.44 9.27 11.73 18.81 15.1 18.23 7.41 16.11 16.15 13.37 16.6 14.1 21.86 14.1 13.61 14.52 15.86 12.93 14.1 22.14 21.35 20.5 15.31 13.59 14.05 17.67 19.21 7.39 15.56 7.39 12.65 17.92 12.79 12.76 16.36 22.06 26.33 18.23 15.31 18.65 15.35 10.87 8.59 16.05 10.96 15.1 16.91 12.65 11.97 23.98 15.1 11.85 12.79 19.67 17.66 9.0 15.01 17.97 15.1 7.79 8.88 19.18 15.25 15.16 17.38 17.63 13.43 15.04 7.87 11.76 6.78 9.0 12.76 12.76 13.47 8.88 13.57 17.6 9.41 9.0 16.96 13.92 12.01 14.25 17.21 12.2 21.12 13.22 17.48 9.2 15.01 15.1 22.98 11.92 11.15 17.38 15.23 23.28 13.47 15.1 11.15 18.57 18.33 15.1 9.86 17.6 19.74 15.1 14.52 8.11 15.45 18.3 21.15 18.23 15.35 20.26 17.4 17.0 16.67 8.27 14.28 14.76 23.18 8.72 22.67 16.33 13.89 17.26 20.74 11.15 15.15 20.89 7.87 8.29 17.13 23.23 14.85 15.1 12.47 14.1 16.43 16.11 15.23 7.39 21.36 20.1 18.39 12.79 15.23 18.65 23.42 8.11 14.1 12.4 9.51 15.1 12.75 19.84 16.09 18.67 8.71 8.13 13.5 12.79 12.55 16.86 14.44 15.26 8.96 15.1 18.33 14.86 15.1 13.81 7.78 15.87 7.78 15.1 16.26 13.65 21.96 23.4 14.52 17.12 22.93 19.67 11.79 14.52 6.45 7.39 14.1 12.55 25.63 16.94 19.39 9.26 13.72 15.23 15.41 18.29 15.16 12.51 8.27 24.58 13.73 21.15 15.1 13.64 18.62 18.0 8.37 17.67 13.44 9.44 13.64 22.06 16.11 16.32 16.79 9.1 11.85 8.35 25.74 16.14 12.66 17.8 21.49 17.92 12.82 17.67 15.89 19.32 15.79 7.78 19.95 15.79 19.89 22.15 23.27 9.45 7.78 11.85 19.28 19.61 16.15 22.99 21.39 13.92 14.09 9.93 15.6 11.9 23.39 22.59 13.8 12.36 13.18 12.28 16.79 8.37 15.16 17.18 11.85 14.52 23.58 19.47 16.12 15.1 15.38 15.23 16.81 21.67 12.82 20.1 7.39 19.23 15.1 21.58 19.85 17.36 18.79 7.39 8.72 17.6 7.39 20.89 12.99 15.1 15.23 20.64 23.76 12.48 14.52 12.13 7.39 13.67 12.43 11.45 13.42 14.61 17.67 20.71 12.92 24.77 5.49 15.1 13.23 22.09 16.12 15.52 15.25 25.63 17.6 14.1 8.11 15.99 10.96 17.42 18.51 15.23 15.46 8.88 23.12 15.73 25.38 7.78 14.11 15.79 7.71 16.79 9.45 16.79 19.74 17.75 15.11 8.51 14.1 16.25 22.54 11.43 13.51 15.81 7.81 7.99 20.8 16.75 15.86 15.63 15.42 14.1 16.07 14.1 9.94 25.78 8.29 15.15 15.1 9.44 15.1 10.14 9.34 16.11 15.51 9.6 16.11 21.57 18.23 21.15 8.91 15.1 17.6 8.72 7.39 7.78 9.34 20.08 15.55 16.07 15.1 21.15 18.2 11.8 16.32 7.87 18.44 14.1 15.23 18.57 18.34 24.48 10.96 11.86 19.8 16.71 23.57 11.85 19.02 21.14 12.83 10.96 15.1 9.23 18.31 15.33 17.89 20.98 14.52 13.76 26.05 13.75 23.14 11.98 10.91 12.48 18.19 25.63 7.78 14.5 13.11 15.38 15.39 21.52 18.12 13.65 12.86 7.78 16.11 22.06 20.87 20.91 14.86 16.32 18.54 8.72 7.78 15.52 22.78 17.6 21.88 8.11 15.04 14.59 23.84 18.78 15.79 18.23 15.23 15.1 14.17 19.71 16.99 23.39 7.78 21.19 17.87 

In [55]:
display(data_merge_Slice.select('freight_value'))

freight_value 13.25 18.12 14.17 17.67 25.61 9.34 15.34 19.5 22.77 14.62 17.05 7.45 16.25 8.29 16.11 22.14 12.69 12.79 13.43 7.57 7.8 11.86 23.93 17.06 12.69 19.05 12.69 9.94 18.05 26.43 18.95 17.11 8.29 13.96 17.67 16.88 12.86 8.72 7.78 18.93 16.79 16.69 16.99 17.95 13.37 17.67 23.28 17.0 15.1 15.1 16.79 10.55 12.78 18.43 16.45 18.3 14.42 12.21 18.54 15.23 11.98 9.13 14.29 8.48 14.09 14.1 21.64 8.27 18.49 10.96 15.25 9.6 8.57 15.1 20.26 7.78 17.63 7.39 22.34 11.53 13.02 16.34 12.69 19.29 19.04 15.65 17.46 14.1 13.65 9.23 16.52 22.56 17.95 12.49 12.48 12.76 20.23 8.29 11.85 9.53 19.05 7.87 7.65 22.59 14.32 10.96 15.24 14.52 17.64 7.39 13.11 15.23 21.6 10.83 15.43 17.26 18.23 9.34 19.53 14.3 18.59 22.85 15.59 16.14 15.1 15.79 20.28 20.98 11.74 16.18 7.67 18.42 12.04 18.61 16.19 7.44 14.0 18.37 13.83 15.1 13.39 18.16 13.72 8.3 8.72 15.1 7.39 7.77 12.69 7.75 18.33 14.04 15.23 13.71 6.0 22.06 14.1 16.11 15.23 8.82 16.94 15.23 8.27 7.39 18.08 18.63 12.71 12.43 24.73 16.79 24.55 17.78 18.53 14.1 15.1 23.07 13.25 7.48 16.11 14.79 19.18 16.73 18.23 14.35 16.2 15.1 15.46 23.19 24.93 18.23 12.13 11.85 12.48 15.76 17.67 13.38 7.71 17.63 16.11 15.1 19.38 16.93 11.31 18.26 19.97 8.88 15.46 16.84 15.14 15.07 16.11 18.59 12.55 22.38 24.14 14.13 11.81 24.32 17.83 18.29 18.23 14.77 18.71 8.88 25.63 23.62 21.73 12.89 18.65 13.08 18.44 23.7 15.1 20.52 22.41 9.36 15.23 19.06 19.32 24.12 24.61 7.89 16.61 20.59 15.44 9.27 11.73 18.81 15.1 18.23 7.41 16.11 16.15 13.37 16.6 14.1 21.86 14.1 13.61 14.52 15.86 12.93 14.1 22.14 21.35 20.5 15.31 13.59 14.05 17.67 19.21 7.39 15.56 7.39 12.65 17.92 12.79 12.76 16.36 22.06 26.33 18.23 15.31 18.65 15.35 10.87 8.59 16.05 10.96 15.1 16.91 12.65 11.97 23.98 15.1 11.85 12.79 19.67 17.66 9.0 15.01 17.97 15.1 7.79 8.88 19.18 15.25 15.16 17.38 17.63 13.43 15.04 7.87 11.76 6.78 9.0 12.76 12.76 13.47 8.88 13.57 17.6 9.41 9.0 16.96 13.92 12.01 14.25 17.21 12.2 21.12 13.22 17.48 9.2 15.01 15.1 22.98 11.92 11.15 17.38 15.23 23.28 13.47 15.1 11.15 18.57 18.33 15.1 9.86 17.6 19.74 15.1 14.52 8.11 15.45 18.3 21.15 18.23 15.35 20.26 17.4 17.0 16.67 8.27 14.28 14.76 23.18 8.72 22.67 16.33 13.89 17.26 20.74 11.15 15.15 20.89 7.87 8.29 17.13 23.23 14.85 15.1 12.47 14.1 16.43 16.11 15.23 7.39 21.36 20.1 18.39 12.79 15.23 18.65 23.42 8.11 14.1 12.4 9.51 15.1 12.75 19.84 16.09 18.67 8.71 8.13 13.5 12.79 12.55 16.86 14.44 15.26 8.96 15.1 18.33 14.86 15.1 13.81 7.78 15.87 7.78 15.1 16.26 13.65 21.96 23.4 14.52 17.12 22.93 19.67 11.79 14.52 6.45 7.39 14.1 12.55 25.63 16.94 19.39 9.26 13.72 15.23 15.41 18.29 15.16 12.51 8.27 24.58 13.73 21.15 15.1 13.64 18.62 18.0 8.37 17.67 13.44 9.44 13.64 22.06 16.11 16.32 16.79 9.1 11.85 8.35 25.74 16.14 12.66 17.8 21.49 17.92 12.82 17.67 15.89 19.32 15.79 7.78 19.95 15.79 19.89 22.15 23.27 9.45 7.78 11.85 19.28 19.61 16.15 22.99 21.39 13.92 14.09 9.93 15.6 11.9 23.39 22.59 13.8 12.36 13.18 12.28 16.79 8.37 15.16 17.18 11.85 14.52 23.58 19.47 16.12 15.1 15.38 15.23 16.81 21.67 12.82 20.1 7.39 19.23 15.1 21.58 19.85 17.36 18.79 7.39 8.72 17.6 7.39 20.89 12.99 15.1 15.23 20.64 23.76 12.48 14.52 12.13 7.39 13.67 12.43 11.45 13.42 14.61 17.67 20.71 12.92 24.77 5.49 15.1 13.23 22.09 16.12 15.52 15.25 25.63 17.6 14.1 8.11 15.99 10.96 17.42 18.51 15.23 15.46 8.88 23.12 15.73 25.38 7.78 14.11 15.79 7.71 16.79 9.45 16.79 19.74 17.75 15.11 8.51 14.1 16.25 22.54 11.43 13.51 15.81 7.81 7.99 20.8 16.75 15.86 15.63 15.42 14.1 16.07 14.1 9.94 25.78 8.29 15.15 15.1 9.44 15.1 10.14 9.34 16.11 15.51 9.6 16.11 21.57 18.23 21.15 8.91 15.1 17.6 8.72 7.39 7.78 9.34 20.08 15.55 16.07 15.1 21.15 18.2 11.8 16.32 7.87 18.44 14.1 15.23 18.57 18.34 24.48 10.96 11.86 19.8 16.71 23.57 11.85 19.02 21.14 12.83 10.96 15.1 9.23 18.31 15.33 17.89 20.98 14.52 13.76 26.05 13.75 23.14 11.98 10.91 12.48 18.19 25.63 7.78 14.5 13.11 15.38 15.39 21.52 18.12 13.65 12.86 7.78 16.11 22.06 20.87 20.91 14.86 16.32 18.54 8.72 7.78 15.52 22.78 17.6 21.88 8.11 15.04 14.59 23.84 18.78 15.79 18.23 15.23 15.1 14.17 19.71 16.99 23.39 7.78 21.19 17.87 

In [56]:
display(data_merge_Slice.select('freight_value')\
        .summary('count',
                'min',
                '25%',
                'mean',
                'stddev',
                '50%',
                '75%',
                '85%',
                '90%',
                '95%',
                '99%',
                'max'))


summary freight_value count 86741 min 5.0 25% 12.69 mean 15.573961794306335 stddev 4.5732571996071005 50% 15.38 75% 18.3 85% 20.14 90% 22.0 95% 23.63 99% 25.91 max 26.72

In [57]:
pandas_df = data_merge_Slice.toPandas()

In [58]:
%python
import seaborn as sns
import matplotlib.pyplot as plt
sns.set(rc={'figure.figsize':(20,20)})

#fig, ax = plt.figure()
sns.heatmap(pandas_df.corr(), xticklabels=pandas_df.corr().columns, yticklabels=pandas_df.corr().columns,cmap='RdBu_r',annot=True, cbar=False)
display()

In [59]:
%python
import seaborn as sns
import matplotlib.pyplot as plt
sns.set(rc={'figure.figsize':(20,20)})

#fig, ax = plt.figure()
sns.heatmap(pandas_df.cov(), xticklabels=pandas_df.cov().columns, yticklabels=pandas_df.cov().columns,cmap='RdBu_r',annot=True, cbar=False)
display()

In [60]:
df.count()

Out[58]: 86741

In [61]:
data_merge_total.count()

Out[59]: 103268

In [62]:
from pyspark.ml.feature import VectorAssembler

In [63]:
assembler    = VectorAssembler(inputCols = df.columns[:-1], outputCol  = 'features')
assembler_Tot = VectorAssembler(inputCols = data_merge_total.columns[:-1], outputCol  = 'features')

In [64]:
df_assembler = assembler.transform(df)
df_assembler_Tot = assembler_Tot.transform(data_merge_total)
display(df_assembler)

volume distancia_sellers_customers order_delivered_carrier_date price payment_value product_weight_g codigo_UF_customers codigo_UF_sellers customer_zip_code_prefix geolocation_lat_customer geolocation_lng_customer seller_zip_code_prefix geolocation_lat_seller geolocation_lng_seller freight_value features 3520 322.33 1502481888 249.9 263.15 200 35 35 15130 -20.820303506184285 -49.5267184606784 13170 -22.823844024822737 -47.26994520496454 13.25 List(1, 14, List(), List(3520.0, 322.33, 1.502481888E9, 249.9, 263.15, 200.0, 35.0, 35.0, 15130.0, -20.820303506184285, -49.5267184606784, 13170.0, -22.823844024822737, -47.26994520496454)) 5508 751.7 1525250820 64.99 259.33 525 53 35 70680 -15.78404999999995 -47.91689999999997 17350 -22.51638966443662 -48.56624997994872 18.12 List(1, 14, List(), List(5508.0, 751.7, 1.52525082E9, 64.99, 259.33, 525.0, 53.0, 35.0, 70680.0, -15.78404999999995, -47.91689999999997, 17350.0, -22.51638966443662, -48.56624997994872)) 6460 288.29 1517250903 165.0 179.17 920 35 35 6362 -23.556164024969256 -46.84471892605726 14070 -21.116559132667774 -47.79365383236194 14.17 List(1, 14, List(), List(6460.0, 288.29, 1.517250903E9, 165.0, 179.17, 920.0, 35.0, 35.0, 6362.0, -23.556164024969256, -46.84471892605726, 14070.0, -21.116559132667774, -47.79365383236194)) 19800 249.69 1505849332 59.9 155.14 1550 31 35 37950 -20.910025107032975 -46.988130451821675 15025 -20.805236807536087 -49.388535432417434 17.67 List(1, 14, List(), List(19800.0, 249.69, 1.505849332E9, 59.9, 155.14, 1550.0, 31.0, 35.0, 37950.0, -20.910025107032975, -46.988130451821675, 15025.0, -20.805236807536087, -49.388535432417434)) 3360 2478.66 1521818200 989.0 1014.61 408 15 35 67140 -1.3292433911310277 -48.39944050923933 6144 -23.566356522909487 -46.799477082578285 25.61 List(1, 14, List(), List(3360.0, 2478.66, 1.5218182E9, 989.0, 1014.61, 408.0, 15.0, 35.0, 67140.0, -1.3292433911310277, -48.39944050923933, 6144.0, -23.566356522909487, -46.799477082578285)) 18000 11.12 1511370534 19.9 29.24 800 35 35 4363 -23.647438351376287 -46.66991915973221 1239 -23.548299317790978 -46.65555908895493 9.34 List(1, 14, List(), List(18000.0, 11.12, 1.511370534E9, 19.9, 29.24, 800.0, 35.0, 35.0, 4363.0, -23.647438351376287, -46.66991915973221, 1239.0, -23.548299317790978, -46.65555908895493)) 21420 952.07 1508191603 85.0 100.34 1700 43 35 90660 -30.05873310574757 -51.19696747654224 14940 -21.76590242683773 -48.824481207427674 15.34 List(1, 14, List(), List(21420.0, 952.07, 1.508191603E9, 85.0, 100.34, 1700.0, 43.0, 35.0, 90660.0, -30.05873310574757, -51.19696747654224, 14940.0, -21.76590242683773, -48.824481207427674)) 21200 900.83 1512473344 89.9 218.8 1825 32 35 29060 -20.281745839027028 -40.29092438008551 14940 -21.76590242683773 -48.824481207427674 19.5 List(1, 14, List(), List(21200.0, 900.83, 1.512473344E9, 89.9, 218.8, 1825.0, 32.0, 35.0, 29060.0, -20.281745839027028, -40.29092438008551, 14940.0, -21.76590242683773, -48.824481207427674)) 4500 1366.31 1534255980 119.9 142.67 304 43 33 96020 -31.775410163194664 -52.345362184026676 25645 -22.546180062655825 -43.20830593734418 22.77 List(1, 14, List(), List(4500.0, 1366.31, 1.53425598E9, 119.9, 142.67, 304.0, 43.0, 33.0, 96020.0, -31.775410163194664, -52.345362184026676, 25645.0, -22.546180062655825, -43.20830593734418)) 3960 942.74 1489739006 64.99 79.61 200 31 35 39560 -16.168399136214365 -42.292471007871654 9015 -23.65535191785441 -46.5280572305095 14.62 List(1, 14, List(), List(3960.0, 942.74, 1.489739006E9, 64.99, 79.61, 200.0, 31.0, 35.0, 39560.0, -16.168399136214365, -42.292471007871654, 9015.0, -23.65535191785441, -46.5280572305095)) 5100 332.22 1490973134 326.66 343.71 2250 33 35 21330 -22.88030689148247 -43.37138460739236 3702 -23.517923280598993 -46.54712945697963 17.05 List(1, 14, List(), List(5100.0, 332.22, 1.490973134E9, 326.66, 343.71, 2250.0, 33.0, 35.0, 21330.0, -22.88030689148247, -43.37138460739236, 3702.0, -23.517923280598993, -46.54712945697963)) 960 100.03 1532436180 26.9 34.35 300 35 35 8440

In [65]:
(df_assembler.count(), len(df_assembler.columns))
(df_assembler_Tot.count(), len(df_assembler_Tot.columns))

Out[63]: (103268, 16)

In [66]:
treino, teste = df_assembler.randomSplit([0.7, 0.3], seed=36)
treino_Tot, teste_Tot = df_assembler_Tot.randomSplit([0.7, 0.3], seed=36)

treino = treino.repartition(2).cache()
treino.count()

teste = teste.repartition(2).cache()
teste.count()

treino_Tot = treino_Tot.repartition(2).cache()
treino_Tot.count()

teste_Tot = teste_Tot.repartition(2).cache()
teste_Tot.count()

Out[64]: 30967

In [67]:
from pyspark.ml.regression import LinearRegression

lr = LinearRegression(labelCol= 'freight_value')

modelo = lr.fit(treino)
modelo_Tot = lr.fit(treino_Tot)

In [68]:
print(f'Coeficientes: {modelo.coefficients}')
print(f'pValues: {modelo.summary.pValues}')
print(f'Intercepto: {modelo.intercept}')

Coeficientes: [3.854961324486048e-05,0.004589604396872106,2.9570948007302126e-08,0.007560053370392344,-0.00024624833807119774,0.0004292651236110857,-0.03252943319950993,-0.06898552473537661,3.8220023422255146e-05,-0.0626924620631924,0.1534100447940982,2.8976237759925614e-05,0.08297431354744307,-0.07089452736409423]
pValues: [0.0, 0.0, 0.0, 0.0, 0.16311229787198966, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
Intercepto: -27.280273621984296

In [69]:
print(f'MAE: {modelo.summary.meanAbsoluteError}') #Erro absoluto do modelo
print(f'RMSE: {modelo.summary.rootMeanSquaredError}') #R2 ao quadrado error em valor
print(f'r2 Ajustado: {modelo.summary.r2adj *100}') #As variaveis que nos temos no modelo explicam 53.33% do modelo

'''
Base Line Metrics

MAE: 5.964145570151102
MSE: 119.27973085177
RMSE: 10.921526031272828
r2 Ajustado: 53.32880323011593'
'''

'''
Após a inclusão do codigo do CEP do vendedor.
Antes do corte de dados, dos outiliers do valor do frete

MAE: 5.742249298528482
MSE: 108.08284389752195
RMSE: 10.396289910228646
r2 Ajustado: 56.504091413487714
'''

maeLR_train  = modelo.summary.meanAbsoluteError
rmseLR_train = modelo.summary.rootMeanSquaredError
r2LR_train   = modelo.summary.r2adj

MAE: 2.318835614326492
RMSE: 3.054588994881714
r2 Ajustado: 55.40230291470822

In [70]:
resultado_teste = modelo.evaluate(teste)
resultado_teste_Tot = modelo_Tot.evaluate(teste_Tot)

In [71]:
print(f'MAE: {resultado_teste.meanAbsoluteError}')
print(f'RMSE: {resultado_teste.rootMeanSquaredError}')
print(f'r2 Ajustado: {resultado_teste.r2adj}')

maeLR_teste  = resultado_teste.meanAbsoluteError
rmseLR_teste = resultado_teste.rootMeanSquaredError
r2LR_teste   = resultado_teste.r2adj

maeLR_teste_Tot  = resultado_teste_Tot.meanAbsoluteError
rmseLR_teste_Tot = resultado_teste_Tot.rootMeanSquaredError
r2LR_teste_Tot   = resultado_teste_Tot.r2adj

MAE: 2.301002436385273
RMSE: 3.032605165346057
r2 Ajustado: 0.5594360716156693

In [73]:
from pyspark.ml import Pipeline
from pyspark.ml.regression import DecisionTreeRegressor
from pyspark.ml.feature import VectorIndexer
from pyspark.ml.evaluation import RegressionEvaluator

featureIndexer = VectorIndexer(inputCol="features", 
                              outputCol="featureIndexer",
                              maxCategories=100).fit(df_assembler)

featureIndexer_Tot = VectorIndexer(inputCol="features", 
                              outputCol="featureIndexer",
                              maxCategories=100).fit(df_assembler_Tot)

dt = DecisionTreeRegressor(featuresCol="featureIndexer", labelCol="freight_value", maxBins=128)
#dt = DecisionTreeRegressor(featuresCol="featureIndexer", labelCol="freight_value", maxBins=50000)

# Chain indexer and tree in a Pipeline
pipeline = Pipeline(stages=[featureIndexer, dt])
pipeline_Tot = Pipeline(stages=[featureIndexer_Tot, dt])

modelarvore = pipeline.fit(treino)
modelarvore_Tot = pipeline_Tot.fit(treino_Tot)

predictions = modelarvore.transform(teste)
predictions_Tot = modelarvore_Tot.transform(teste_Tot)

In [74]:
display(predictions.select("prediction", "freight_value", "features"))

prediction freight_value features 17.977098366881886 15.79 List(1, 14, List(), List(1760.0, 1334.18, 1.512778381E9, 22.4, 38.19, 50.0, 51.0, 35.0, 78115.0, -15.630708686678625, -56.103974076190774, 3880.0, -23.507968714957602, -46.486797454065425)) 8.54010985178727 7.71 List(1, 14, List(), List(1920.0, 1.67, 1.52631108E9, 39.9, 47.61, 100.0, 31.0, 31.0, 31170.0, -19.88616931560503, -43.918037920334896, 31140.0, -19.892338512349244, -43.9326199797449)) 12.724124112663157 12.15 List(1, 14, List(), List(23625.0, 228.54, 1.510154079E9, 93.55, 105.7, 400.0, 35.0, 35.0, 13272.0, -22.958132362908653, -47.01404961028068, 14940.0, -21.76590242683773, -48.824481207427674)) 17.977098366881886 15.79 List(1, 14, List(), List(1920.0, 1454.03, 1.503332819E9, 29.9, 45.69, 400.0, 29.0, 35.0, 41815.0, -12.994583582396373, -38.47371666208345, 9350.0, -23.672056986410002, -46.44219782970755)) 12.724124112663157 12.79 List(1, 14, List(), List(1188.0, 471.5, 1.53026058E9, 18.9, 31.69, 50.0, 35.0, 35.0, 16021.0, -21.227637259359184, -50.45979181459947, 1511.0, -23.56462684762538, -46.63248269259636)) 15.537384273937853 13.72 List(1, 14, List(), List(13608.0, 303.6, 1.498835608E9, 99.99, 113.71, 1400.0, 35.0, 35.0, 4671.0, -23.658998521236047, -46.69142628475392, 14940.0, -21.76590242683773, -48.824481207427674)) 17.835155058464668 18.23 List(1, 14, List(), List(2800.0, 437.92, 1.522326729E9, 14.4, 32.63, 150.0, 42.0, 35.0, 88341.0, -27.034095547340915, -48.64332396399446, 1212.0, -23.537083672773957, -46.639449309048416)) 20.994241354975312 16.79 List(1, 14, List(), List(816.0, 1571.41, 1.510090109E9, 24.99, 41.78, 300.0, 29.0, 35.0, 48770.0, -11.489509493227507, -38.998607624385585, 4160.0, -23.625863266720533, -46.61180698251485)) 12.724124112663157 12.79 List(1, 14, List(), List(4096.0, 243.65, 1.52527446E9, 44.9, 57.69, 550.0, 35.0, 35.0, 1422.0, -23.558810563967953, -46.66710524617697, 18683.0, -22.59596015457897, -48.80665359538019)) 12.724124112663157 12.84 List(1, 14, List(), List(816.0, 377.62, 1.53374556E9, 24.99, 37.83, 300.0, 35.0, 35.0, 17526.0, -22.241390417040495, -49.97916884723654, 4160.0, -23.625863266720533, -46.61180698251485)) 20.41730425055929 15.66 List(1, 14, List(), List(15750.0, 993.86, 1.496227956E9, 129.99, 145.65, 1400.0, 43.0, 35.0, 97060.0, -29.700766564465592, -53.80292076818464, 3426.0, -23.550569408680975, -46.54088389992436)) 15.991694618272838 14.17 List(1, 14, List(), List(2880.0, 520.68, 1.502219821E9, 34.0, 206.31, 300.0, 35.0, 31.0, 9510.0, -23.611305206215025, -46.5712284440821, 35700.0, -19.462165765780032, -44.23699023679241)) 20.994241354975312 22.06 List(1, 14, List(), List(5355.0, 1824.28, 1.52716074E9, 9.0, 62.12, 150.0, 29.0, 35.0, 48608.0, -9.400351685154615, -38.21546231037806, 9850.0, -23.730523104622396, -46.57756736288881)) 17.977098366881886 19.49 List(1, 14, List(), List(4048.0, 1323.17, 1.505251536E9, 315.0, 334.49, 500.0, 21.0, 29.0, 65061.0, -2.5320256974315485, -44.24520462891361, 42738.0, -12.897090191243207, -38.33828105133945)) 17.835155058464668 15.24 List(1, 14, List(), List(8000.0, 491.49, 1.52993442E9, 19.99, 136.91, 150.0, 31.0, 35.0, 30411.0, -19.921914973916515, -43.95831084234526, 4265.0, -23.58974171521244, -46.614703714855146)) 17.516226685796283 13.67 List(1, 14, List(), List(48552.0, 60.39, 1.512073661E9, 159.9, 173.57, 8200.0, 35.0, 35.0, 13256.0, -23.012171079607057, -46.85425029097554, 2066.0, -23.50546246073055, -46.606927982370635)) 17.977098366881886 22.13 List(1, 14, List(), List(561.0, 1462.03, 1.513046106E9, 189.9, 212.03, 450.0, 35.0, 29.0, 3734.0, -23.510657419931878, -46.52425462101101, 42738.0, -12.897090191243207, -38.33828105133945)) 15.991694618272838 15.79 List(1, 14, List(), List(2160.0, 875.04, 1.518722043E9, 18.0, 33.79, 200.0, 35.0, 53.0, 8330.0, -23.619876903975946, -46.4641611021409, 71825.0, -15.886620476289508, -48.01443185354944)) 15.538277878175835 15.1 List(1, 14, List(), List(896.0, 778.14, 1.504131156E9, 7.49, 22.59, 200.0, 41.0, 35.0, 85880.0, -2

In [75]:
evaluator = RegressionEvaluator(
    labelCol="freight_value", predictionCol="prediction", metricName="rmse")
rmse = evaluator.evaluate(predictions)
print("Root Mean Squared Error (RMSE) on test data = %g" % rmse)

evaluator = RegressionEvaluator(
    labelCol="freight_value", predictionCol="prediction", metricName="mae")
mae = evaluator.evaluate(predictions)
print("MAE = %g" % mae)

evaluator = RegressionEvaluator(
    labelCol="freight_value", predictionCol="prediction", metricName="r2")
r2 = evaluator.evaluate(predictions)
print("R2 = %g" % r2)

maeAR_teste  = mae
rmseAR_teste = rmse
r2AR_teste   = r2

treeModel = modelarvore.stages[1]
#Base cheia
#----------------------------------------------------------------------------
evaluator = RegressionEvaluator(
    labelCol="freight_value", predictionCol="prediction", metricName="rmse")
rmse = evaluator.evaluate(predictions_Tot)
print("Root Mean Squared Error (RMSE) on test data = %g" % rmse)

evaluator = RegressionEvaluator(
    labelCol="freight_value", predictionCol="prediction", metricName="mae")
mae = evaluator.evaluate(predictions_Tot)
print("MAE = %g" % mae)

evaluator = RegressionEvaluator(
    labelCol="freight_value", predictionCol="prediction", metricName="r2")
r2 = evaluator.evaluate(predictions_Tot)
print("R2 = %g" % r2)

maeAR_teste_Tot  = mae
rmseAR_teste_Tot = rmse
r2AR_teste_Tot   = r2

Root Mean Squared Error (RMSE) on test data = 2.65278
MAE = 1.90685
R2 = 0.663064
Root Mean Squared Error (RMSE) on test data = 10.1865
MAE = 5.05011
R2 = 0.59481

In [76]:
display(treeModel)

treeNode {"index":31,"featureType":"continuous","prediction":null,"threshold":164.07999999999998,"categories":null,"feature":1,"overflow":false} {"index":15,"featureType":"continuous","prediction":null,"threshold":1152.0,"categories":null,"feature":5,"overflow":false} {"index":7,"featureType":"continuous","prediction":null,"threshold":406.5,"categories":null,"feature":5,"overflow":false} {"index":3,"featureType":"continuous","prediction":null,"threshold":101.16,"categories":null,"feature":1,"overflow":false} {"index":1,"featureType":"continuous","prediction":null,"threshold":209.945,"categories":null,"feature":3,"overflow":false} {"index":0,"featureType":null,"prediction":8.54010985178727,"threshold":null,"categories":null,"feature":null,"overflow":false} {"index":2,"featureType":null,"prediction":11.238055555555547,"threshold":null,"categories":null,"feature":null,"overflow":false} {"index":5,"featureType":"continuous","prediction":null,"threshold":14024.5,"categories":null,"feature":8,"overflow":false} {"index":4,"featureType":null,"prediction":9.67871235721703,"threshold":null,"categories":null,"feature":null,"overflow":false} {"index":6,"featureType":null,"prediction":12.658611987381711,"threshold":null,"categories":null,"feature":null,"overflow":false} {"index":11,"featureType":"continuous","prediction":null,"threshold":13508.0,"categories":null,"feature":8,"overflow":false} {"index":9,"featureType":"continuous","prediction":null,"threshold":212.115,"categories":null,"feature":4,"overflow":false} {"index":8,"featureType":null,"prediction":10.010917278185458,"threshold":null,"categories":null,"feature":null,"overflow":false} {"index":10,"featureType":null,"prediction":12.131455696202512,"threshold":null,"categories":null,"feature":null,"overflow":false} {"index":13,"featureType":"continuous","prediction":null,"threshold":68.56,"categories":null,"feature":1,"overflow":false} {"index":12,"featureType":null,"prediction":10.544441558441557,"threshold":null,"categories":null,"feature":null,"overflow":false} {"index":14,"featureType":null,"prediction":13.178352490421455,"threshold":null,"categories":null,"feature":null,"overflow":false} {"index":23,"featureType":"continuous","prediction":null,"threshold":4437.5,"categories":null,"feature":5,"overflow":false} {"index":19,"featureType":"continuous","prediction":null,"threshold":157.995,"categories":null,"feature":3,"overflow":false} {"index":17,"featureType":"continuous","prediction":null,"threshold":95.18,"categories":null,"feature":1,"overflow":false} {"index":16,"featureType":null,"prediction":12.432480359147027,"threshold":null,"categories":null,"feature":null,"overflow":false} {"index":18,"featureType":null,"prediction":14.085889655172414,"threshold":null,"categories":null,"feature":null,"overflow":false} {"index":21,"featureType":"continuous","prediction":null,"threshold":600.0450000000001,"categories":null,"feature":4,"overflow":false} {"index":20,"featureType":null,"prediction":14.651058451816745,"threshold":null,"categories":null,"feature":null,"overflow":false} {"index":22,"featureType":null,"prediction":18.362923076923078,"threshold":null,"categories":null,"feature":null,"overflow":false} {"index":27,"featureType":"continuous","prediction":null,"threshold":61960.0,"categories":null,"feature":0,"overflow":false} {"index":25,"featureType":"continuous","prediction":null,"threshold":113.945,"categories":null,"feature":3,"overflow":false} {"index":24,"featureType":null,"prediction":14.671680532445924,"threshold":null,"categories":null,"feature":null,"overflow":false} {"index":26,"featureType":null,"prediction":17.516226685796283,"threshold":null,"categories":null,"feature":null,"overflow":false} {"index":29,"featureType":"continuous","prediction":null,"threshold":5837.5,"categories":null,"feature":5,"overflow":false} {"index":28,"featureType":null,"prediction":16.52782608695652,"threshold":null,"categories":null,"feature":null,"overflow":false} {"index":30,"featureType":null

In [78]:
from pyspark.ml import Pipeline
from pyspark.ml.regression import GBTRegressor
from pyspark.ml.feature import VectorIndexer
from pyspark.ml.evaluation import RegressionEvaluator

featureIndexer =\
    VectorIndexer(inputCol="features", outputCol="indexedFeatures", maxCategories=100).fit(df_assembler)

featureIndexer_Tot =\
    VectorIndexer(inputCol="features", outputCol="indexedFeatures", maxCategories=100).fit(df_assembler_Tot)

# Train a GBT model.
gbt = GBTRegressor(featuresCol="indexedFeatures", labelCol="freight_value",  maxIter=10)

# Chain indexer and GBT in a Pipeline
pipeline = Pipeline(stages=[featureIndexer, gbt])
pipeline_Tot = Pipeline(stages=[featureIndexer_Tot, gbt])

# Train model.  This also runs the indexer.
modelgbt = pipeline.fit(treino)
modelgbt_Tot = pipeline_Tot.fit(treino_Tot)

predictions = modelgbt.transform(teste)
predictions_Tot = modelgbt_Tot.transform(teste_Tot)

In [79]:
display(predictions.select("prediction", "freight_value", "features"))

prediction freight_value features 17.862453296918545 15.79 List(1, 14, List(), List(1760.0, 1334.18, 1.512778381E9, 22.4, 38.19, 50.0, 51.0, 35.0, 78115.0, -15.630708686678625, -56.103974076190774, 3880.0, -23.507968714957602, -46.486797454065425)) 8.466288841064552 7.71 List(1, 14, List(), List(1920.0, 1.67, 1.52631108E9, 39.9, 47.61, 100.0, 31.0, 31.0, 31170.0, -19.88616931560503, -43.918037920334896, 31140.0, -19.892338512349244, -43.9326199797449)) 12.59411818292913 12.15 List(1, 14, List(), List(23625.0, 228.54, 1.510154079E9, 93.55, 105.7, 400.0, 35.0, 35.0, 13272.0, -22.958132362908653, -47.01404961028068, 14940.0, -21.76590242683773, -48.824481207427674)) 17.4616184864709 15.79 List(1, 14, List(), List(1920.0, 1454.03, 1.503332819E9, 29.9, 45.69, 400.0, 29.0, 35.0, 41815.0, -12.994583582396373, -38.47371666208345, 9350.0, -23.672056986410002, -46.44219782970755)) 12.109840714004203 12.79 List(1, 14, List(), List(1188.0, 471.5, 1.53026058E9, 18.9, 31.69, 50.0, 35.0, 35.0, 16021.0, -21.227637259359184, -50.45979181459947, 1511.0, -23.56462684762538, -46.63248269259636)) 15.154179005044295 13.72 List(1, 14, List(), List(13608.0, 303.6, 1.498835608E9, 99.99, 113.71, 1400.0, 35.0, 35.0, 4671.0, -23.658998521236047, -46.69142628475392, 14940.0, -21.76590242683773, -48.824481207427674)) 17.43372194904112 18.23 List(1, 14, List(), List(2800.0, 437.92, 1.522326729E9, 14.4, 32.63, 150.0, 42.0, 35.0, 88341.0, -27.034095547340915, -48.64332396399446, 1212.0, -23.537083672773957, -46.639449309048416)) 17.525183660437342 16.79 List(1, 14, List(), List(816.0, 1571.41, 1.510090109E9, 24.99, 41.78, 300.0, 29.0, 35.0, 48770.0, -11.489509493227507, -38.998607624385585, 4160.0, -23.625863266720533, -46.61180698251485)) 15.527953992337023 12.79 List(1, 14, List(), List(4096.0, 243.65, 1.52527446E9, 44.9, 57.69, 550.0, 35.0, 35.0, 1422.0, -23.558810563967953, -46.66710524617697, 18683.0, -22.59596015457897, -48.80665359538019)) 12.109840714004203 12.84 List(1, 14, List(), List(816.0, 377.62, 1.53374556E9, 24.99, 37.83, 300.0, 35.0, 35.0, 17526.0, -22.241390417040495, -49.97916884723654, 4160.0, -23.625863266720533, -46.61180698251485)) 17.96934275010964 15.66 List(1, 14, List(), List(15750.0, 993.86, 1.496227956E9, 129.99, 145.65, 1400.0, 43.0, 35.0, 97060.0, -29.700766564465592, -53.80292076818464, 3426.0, -23.550569408680975, -46.54088389992436)) 15.158121877439418 14.17 List(1, 14, List(), List(2880.0, 520.68, 1.502219821E9, 34.0, 206.31, 300.0, 35.0, 31.0, 9510.0, -23.611305206215025, -46.5712284440821, 35700.0, -19.462165765780032, -44.23699023679241)) 20.225625533316737 22.06 List(1, 14, List(), List(5355.0, 1824.28, 1.52716074E9, 9.0, 62.12, 150.0, 29.0, 35.0, 48608.0, -9.400351685154615, -38.21546231037806, 9850.0, -23.730523104622396, -46.57756736288881)) 23.09314528778215 19.49 List(1, 14, List(), List(4048.0, 1323.17, 1.505251536E9, 315.0, 334.49, 500.0, 21.0, 29.0, 65061.0, -2.5320256974315485, -44.24520462891361, 42738.0, -12.897090191243207, -38.33828105133945)) 17.993485923854056 15.24 List(1, 14, List(), List(8000.0, 491.49, 1.52993442E9, 19.99, 136.91, 150.0, 31.0, 35.0, 30411.0, -19.921914973916515, -43.95831084234526, 4265.0, -23.58974171521244, -46.614703714855146)) 19.715411150114264 13.67 List(1, 14, List(), List(48552.0, 60.39, 1.512073661E9, 159.9, 173.57, 8200.0, 35.0, 35.0, 13256.0, -23.012171079607057, -46.85425029097554, 2066.0, -23.50546246073055, -46.606927982370635)) 22.73657680947659 22.13 List(1, 14, List(), List(561.0, 1462.03, 1.513046106E9, 189.9, 212.03, 450.0, 35.0, 29.0, 3734.0, -23.510657419931878, -46.52425462101101, 42738.0, -12.897090191243207, -38.33828105133945)) 16.058236319016146 15.79 List(1, 14, List(), List(2160.0, 875.04, 1.518722043E9, 18.0, 33.79, 200.0, 35.0, 53.0, 8330.0, -23.619876903975946, -46.4641611021409, 71825.0, -15.886620476289508, -48.01443185354944)) 15.06802297486727 15.1 List(1, 14, List(), List(896.0, 778.14, 1.504131156E9, 7.49, 22.59, 200.0, 41.0, 35.0, 85880.0, -25.1429

In [80]:
# Select (prediction, true label) and compute test error
evaluator = RegressionEvaluator(
    labelCol="freight_value", predictionCol="prediction", metricName="mae")
mae = evaluator.evaluate(predictions)
print("MAE = %g" % mae)

evaluator = RegressionEvaluator(
    labelCol="freight_value", predictionCol="prediction", metricName="rmse")
rmse = evaluator.evaluate(predictions)
print("Root Mean Squared Error (RMSE) on test data = %g" % rmse)

evaluator = RegressionEvaluator(
    labelCol="freight_value", predictionCol="prediction", metricName="r2")
r2 = evaluator.evaluate(predictions)
print("R2 = %g" % r2)

maeGBT_teste  = mae
rmseGBT_teste = rmse
r2GBT_teste   = r2

gbtModel = modelgbt.stages[1]
print(gbtModel)  # summary only

#Base Cheia
#------------------------------------------------------------------------------
# Select (prediction, true label) and compute test error
evaluator = RegressionEvaluator(
    labelCol="freight_value", predictionCol="prediction", metricName="mae")
mae = evaluator.evaluate(predictions_Tot)
print("MAE = %g" % mae)

evaluator = RegressionEvaluator(
    labelCol="freight_value", predictionCol="prediction", metricName="rmse")
rmse = evaluator.evaluate(predictions_Tot)
print("Root Mean Squared Error (RMSE) on test data = %g" % rmse)

evaluator = RegressionEvaluator(
    labelCol="freight_value", predictionCol="prediction", metricName="r2")
r2 = evaluator.evaluate(predictions_Tot)
print("R2 = %g" % r2)

maeGBT_teste_Tot  = mae
rmseGBT_teste_Tot = rmse
r2GBT_teste_Tot   = r2


MAE = 1.68297
Root Mean Squared Error (RMSE) on test data = 2.43461
R2 = 0.716206
GBTRegressionModel (uid=GBTRegressor_34e33c9f226f) with 10 trees
MAE = 4.47354
Root Mean Squared Error (RMSE) on test data = 9.21983
R2 = 0.668062

In [82]:
from pyspark.ml import Pipeline
from pyspark.ml.regression import RandomForestRegressor
from pyspark.ml.feature import VectorIndexer
from pyspark.ml.evaluation import RegressionEvaluator

# Automatically identify categorical features, and index them.
# Set maxCategories so features with > 4 distinct values are treated as continuous.
featureIndexer =\
    VectorIndexer(inputCol="features", outputCol="indexedFeatures", maxCategories=100).fit(df_assembler)

featureIndexer_Tot =\
    VectorIndexer(inputCol="features", outputCol="indexedFeatures", maxCategories=100).fit(df_assembler_Tot)

# Train a RandomForest model.
rf = RandomForestRegressor(featuresCol="indexedFeatures", labelCol="freight_value")

# Chain indexer and forest in a Pipeline
pipeline = Pipeline(stages=[featureIndexer, rf])
pipeline_Tot = Pipeline(stages=[featureIndexer_Tot, rf])

# Train model.  This also runs the indexer.
modelrandom = pipeline.fit(treino)
modelrandom_Tot = pipeline_Tot.fit(treino_Tot)

# Make predictions.
predictions = modelrandom.transform(teste)
predictions_Tot = modelrandom_Tot.transform(teste_Tot)



In [83]:
display(predictions.select("prediction", "freight_value", "features"))

prediction freight_value features 18.393397837606457 15.79 List(1, 14, List(), List(1760.0, 1334.18, 1.512778381E9, 22.4, 38.19, 50.0, 51.0, 35.0, 78115.0, -15.630708686678625, -56.103974076190774, 3880.0, -23.507968714957602, -46.486797454065425)) 9.755507161304253 7.71 List(1, 14, List(), List(1920.0, 1.67, 1.52631108E9, 39.9, 47.61, 100.0, 31.0, 31.0, 31170.0, -19.88616931560503, -43.918037920334896, 31140.0, -19.892338512349244, -43.9326199797449)) 13.562130876324279 12.15 List(1, 14, List(), List(23625.0, 228.54, 1.510154079E9, 93.55, 105.7, 400.0, 35.0, 35.0, 13272.0, -22.958132362908653, -47.01404961028068, 14940.0, -21.76590242683773, -48.824481207427674)) 18.700208264556824 15.79 List(1, 14, List(), List(1920.0, 1454.03, 1.503332819E9, 29.9, 45.69, 400.0, 29.0, 35.0, 41815.0, -12.994583582396373, -38.47371666208345, 9350.0, -23.672056986410002, -46.44219782970755)) 13.40790819003261 12.79 List(1, 14, List(), List(1188.0, 471.5, 1.53026058E9, 18.9, 31.69, 50.0, 35.0, 35.0, 16021.0, -21.227637259359184, -50.45979181459947, 1511.0, -23.56462684762538, -46.63248269259636)) 14.130497829227048 13.72 List(1, 14, List(), List(13608.0, 303.6, 1.498835608E9, 99.99, 113.71, 1400.0, 35.0, 35.0, 4671.0, -23.658998521236047, -46.69142628475392, 14940.0, -21.76590242683773, -48.824481207427674)) 16.978933119795744 18.23 List(1, 14, List(), List(2800.0, 437.92, 1.522326729E9, 14.4, 32.63, 150.0, 42.0, 35.0, 88341.0, -27.034095547340915, -48.64332396399446, 1212.0, -23.537083672773957, -46.639449309048416)) 19.438492092591567 16.79 List(1, 14, List(), List(816.0, 1571.41, 1.510090109E9, 24.99, 41.78, 300.0, 29.0, 35.0, 48770.0, -11.489509493227507, -38.998607624385585, 4160.0, -23.625863266720533, -46.61180698251485)) 13.552662680561397 12.79 List(1, 14, List(), List(4096.0, 243.65, 1.52527446E9, 44.9, 57.69, 550.0, 35.0, 35.0, 1422.0, -23.558810563967953, -46.66710524617697, 18683.0, -22.59596015457897, -48.80665359538019)) 13.40790819003261 12.84 List(1, 14, List(), List(816.0, 377.62, 1.53374556E9, 24.99, 37.83, 300.0, 35.0, 35.0, 17526.0, -22.241390417040495, -49.97916884723654, 4160.0, -23.625863266720533, -46.61180698251485)) 18.564751137445224 15.66 List(1, 14, List(), List(15750.0, 993.86, 1.496227956E9, 129.99, 145.65, 1400.0, 43.0, 35.0, 97060.0, -29.700766564465592, -53.80292076818464, 3426.0, -23.550569408680975, -46.54088389992436)) 15.868525270846035 14.17 List(1, 14, List(), List(2880.0, 520.68, 1.502219821E9, 34.0, 206.31, 300.0, 35.0, 31.0, 9510.0, -23.611305206215025, -46.5712284440821, 35700.0, -19.462165765780032, -44.23699023679241)) 20.697341395859574 22.06 List(1, 14, List(), List(5355.0, 1824.28, 1.52716074E9, 9.0, 62.12, 150.0, 29.0, 35.0, 48608.0, -9.400351685154615, -38.21546231037806, 9850.0, -23.730523104622396, -46.57756736288881)) 20.85702002084721 19.49 List(1, 14, List(), List(4048.0, 1323.17, 1.505251536E9, 315.0, 334.49, 500.0, 21.0, 29.0, 65061.0, -2.5320256974315485, -44.24520462891361, 42738.0, -12.897090191243207, -38.33828105133945)) 17.54724175567038 15.24 List(1, 14, List(), List(8000.0, 491.49, 1.52993442E9, 19.99, 136.91, 150.0, 31.0, 35.0, 30411.0, -19.921914973916515, -43.95831084234526, 4265.0, -23.58974171521244, -46.614703714855146)) 18.050552250323058 13.67 List(1, 14, List(), List(48552.0, 60.39, 1.512073661E9, 159.9, 173.57, 8200.0, 35.0, 35.0, 13256.0, -23.012171079607057, -46.85425029097554, 2066.0, -23.50546246073055, -46.606927982370635)) 19.191583789567424 22.13 List(1, 14, List(), List(561.0, 1462.03, 1.513046106E9, 189.9, 212.03, 450.0, 35.0, 29.0, 3734.0, -23.510657419931878, -46.52425462101101, 42738.0, -12.897090191243207, -38.33828105133945)) 16.679940347287335 15.79 List(1, 14, List(), List(2160.0, 875.04, 1.518722043E9, 18.0, 33.79, 200.0, 35.0, 53.0, 8330.0, -23.619876903975946, -46.4641611021409, 71825.0, -15.886620476289508, -48.01443185354944)) 16.250816198258942 15.1 List(1, 14, List(), List(896.0, 778.14, 1.504131156E9, 7.49, 22.59, 200.0, 41.0, 35.0, 85880.0, -25.

In [84]:
evaluator = RegressionEvaluator(
    labelCol="freight_value", predictionCol="prediction", metricName="rmse")
rmse = evaluator.evaluate(predictions)
print("Root Mean Squared Error (RMSE) on test data = %g" % rmse)

evaluator = RegressionEvaluator(
    labelCol="freight_value", predictionCol="prediction", metricName="mae")
mae = evaluator.evaluate(predictions)
print("MAE = %g" % mae)

evaluator = RegressionEvaluator(
    labelCol="freight_value", predictionCol="prediction", metricName="r2")
r2 = evaluator.evaluate(predictions)
print("R2 = %g" % r2)

maeRFR_teste  = mae
rmseRFR_teste = rmse
r2RFR_teste   = r2

rfModel = modelrandom.stages[1]
print(rfModel)  # summary only

#Base cheia
#----------------------------------------------------------------------------

# Select (prediction, true label) and compute test error
evaluator = RegressionEvaluator(
    labelCol="freight_value", predictionCol="prediction", metricName="rmse")
rmse = evaluator.evaluate(predictions_Tot)
print("Root Mean Squared Error (RMSE) on test data = %g" % rmse)

evaluator = RegressionEvaluator(
    labelCol="freight_value", predictionCol="prediction", metricName="mae")
mae = evaluator.evaluate(predictions_Tot)
print("MAE = %g" % mae)

evaluator = RegressionEvaluator(
    labelCol="freight_value", predictionCol="prediction", metricName="r2")
r2 = evaluator.evaluate(predictions_Tot)
print("R2 = %g" % r2)

maeRFR_teste_Tot  = mae
rmseRFR_teste_Tot = rmse
r2RFR_teste_Tot   = r2


Root Mean Squared Error (RMSE) on test data = 2.5947
MAE = 1.89976
R2 = 0.677658
RandomForestRegressionModel (uid=RandomForestRegressor_33fcff286d78) with 20 trees
Root Mean Squared Error (RMSE) on test data = 9.91972
MAE = 4.86586
R2 = 0.615753

In [86]:
from pyspark.ml.regression import GeneralizedLinearRegression

glr = GeneralizedLinearRegression(family="gaussian", link="identity", maxIter=10, regParam=0.3, labelCol="freight_value")

# Fit the model
modelgau = glr.fit(treino)
modelgau_Tot = glr.fit(treino_Tot)

# Print the coefficients and intercept for generalized linear regression model
print("Coefficients: " + str(modelgau.coefficients))
print("Intercept: " + str(modelgau.intercept))

# Summarize the model over the training set and print out some metrics
summary = modelgau.summary
print("Coefficient Standard Errors: " + str(summary.coefficientStandardErrors))
print("T Values: " + str(summary.tValues))
print("P Values: " + str(summary.pValues))
print("Dispersion: " + str(summary.dispersion))
print("Null Deviance: " + str(summary.nullDeviance))
print("Residual Degree Of Freedom Null: " + str(summary.residualDegreeOfFreedomNull))
print("Deviance: " + str(summary.deviance))
print("Residual Degree Of Freedom: " + str(summary.residualDegreeOfFreedom))
print("AIC: " + str(summary.aic))
print("Deviance Residuals: ")
summary.residuals().show()

Coefficients: [3.845182367667858e-05,0.004091591558668828,2.645645741108663e-08,0.006205244489818924,0.0008463497606445594,0.00039942589999794945,-0.03149875773167487,-0.04840333230566717,3.832581099547401e-05,-0.02315450494474785,0.13505466319424736,2.724413229636999e-05,0.08385952945830286,-0.06735581264227666]
Intercept: -22.804139003576605
Coefficient Standard Errors: [1.0869493457827625e-06, 3.911403005904771e-05, 9.164736868740992e-10, 0.00017398134335989564, 0.00014837943601013828, 7.109960543602912e-06, 0.002877427101304714, 0.005157048991739295, 5.851779936083809e-07, 0.003692292261890076, 0.004394135143610385, 5.724668301357295e-07, 0.005619428345815974, 0.007192071019295959, 1.425628466846693]
T Values: [35.37591133006078, 104.60674986678792, 28.8676672227482, 35.666148852425124, 5.703955907924675, 56.17835676420558, -10.946848216377877, -9.385858537159717, 65.49427937155617, -6.271037962984845, 30.73520926879855, 47.59076135452341, 14.92314240838068, -9.365287475827818, -15.99584992436103]
P Values: [0.0, 0.0, 0.0, 0.0, 1.1760026286111724e-08, 0.0, 0.0, 0.0, 0.0, 3.610534093922979e-10, 0.0, 0.0, 0.0, 0.0, 0.0]
Dispersion: 9.380647591291037
Null Deviance: 1271693.4458404006
Residual Degree Of Freedom Null: 60769
Deviance: 569921.244408887
Residual Degree Of Freedom: 60755
AIC: 308517.47506341356
Deviance Residuals: 
+--------------------+
 devianceResiduals|
+--------------------+
 1.2994575989801156|
 0.2052320925302915|
 5.321163311449336|
 -1.7310581111339527|
 0.6517491160841402|
 1.604121045864666|
 -0.5408370555954232|
 0.10336514252763962|
 4.779547753196695|
 2.186750672510204|
 0.403298256029899|
 -3.1727032861075193|
 -3.8053724157481286|
 3.99371635071466|
 -4.474282964754853|
 -1.9111446782551695|
 -2.7577175440409825|
 -1.1783739583782662|
-0.05350471970370...|
 0.13564311398095086|
+--------------------+
only showing top 20 rows

In [87]:
predictions = modelgau.transform(teste)
predictions_Tot = modelgau_Tot.transform(teste_Tot)

In [88]:
display(predictions.select("prediction", "freight_value", "features"))

prediction freight_value features 16.680085017872198 15.79 List(1, 14, List(), List(1760.0, 1334.18, 1.512778381E9, 22.4, 38.19, 50.0, 51.0, 35.0, 78115.0, -15.630708686678625, -56.103974076190774, 3880.0, -23.507968714957602, -46.486797454065425)) 13.37123887343979 7.71 List(1, 14, List(), List(1920.0, 1.67, 1.52631108E9, 39.9, 47.61, 100.0, 31.0, 31.0, 31170.0, -19.88616931560503, -43.918037920334896, 31140.0, -19.892338512349244, -43.9326199797449)) 13.587001067918916 12.15 List(1, 14, List(), List(23625.0, 228.54, 1.510154079E9, 93.55, 105.7, 400.0, 35.0, 35.0, 13272.0, -22.958132362908653, -47.01404961028068, 14940.0, -21.76590242683773, -48.824481207427674)) 18.87342150184247 15.79 List(1, 14, List(), List(1920.0, 1454.03, 1.503332819E9, 29.9, 45.69, 400.0, 29.0, 35.0, 41815.0, -12.994583582396373, -38.47371666208345, 9350.0, -23.672056986410002, -46.44219782970755)) 12.520218327320944 12.79 List(1, 14, List(), List(1188.0, 471.5, 1.53026058E9, 18.9, 31.69, 50.0, 35.0, 35.0, 16021.0, -21.227637259359184, -50.45979181459947, 1511.0, -23.56462684762538, -46.63248269259636)) 13.385823995792489 13.72 List(1, 14, List(), List(13608.0, 303.6, 1.498835608E9, 99.99, 113.71, 1400.0, 35.0, 35.0, 4671.0, -23.658998521236047, -46.69142628475392, 14940.0, -21.76590242683773, -48.824481207427674)) 15.17335246224771 18.23 List(1, 14, List(), List(2800.0, 437.92, 1.522326729E9, 14.4, 32.63, 150.0, 42.0, 35.0, 88341.0, -27.034095547340915, -48.64332396399446, 1212.0, -23.537083672773957, -46.639449309048416)) 19.451014789954453 16.79 List(1, 14, List(), List(816.0, 1571.41, 1.510090109E9, 24.99, 41.78, 300.0, 29.0, 35.0, 48770.0, -11.489509493227507, -38.998607624385585, 4160.0, -23.625863266720533, -46.61180698251485)) 12.65309630005412 12.79 List(1, 14, List(), List(4096.0, 243.65, 1.52527446E9, 44.9, 57.69, 550.0, 35.0, 35.0, 1422.0, -23.558810563967953, -46.66710524617697, 18683.0, -22.59596015457897, -48.80665359538019)) 12.568544350745373 12.84 List(1, 14, List(), List(816.0, 377.62, 1.53374556E9, 24.99, 37.83, 300.0, 35.0, 35.0, 17526.0, -22.241390417040495, -49.97916884723654, 4160.0, -23.625863266720533, -46.61180698251485)) 18.287833424343102 15.66 List(1, 14, List(), List(15750.0, 993.86, 1.496227956E9, 129.99, 145.65, 1400.0, 43.0, 35.0, 97060.0, -29.700766564465592, -53.80292076818464, 3426.0, -23.550569408680975, -46.54088389992436)) 14.024554396972672 14.17 List(1, 14, List(), List(2880.0, 520.68, 1.502219821E9, 34.0, 206.31, 300.0, 35.0, 31.0, 9510.0, -23.611305206215025, -46.5712284440821, 35700.0, -19.462165765780032, -44.23699023679241)) 21.165017187874003 22.06 List(1, 14, List(), List(5355.0, 1824.28, 1.52716074E9, 9.0, 62.12, 150.0, 29.0, 35.0, 48608.0, -9.400351685154615, -38.21546231037806, 9850.0, -23.730523104622396, -46.57756736288881)) 22.20304235138131 19.49 List(1, 14, List(), List(4048.0, 1323.17, 1.505251536E9, 315.0, 334.49, 500.0, 21.0, 29.0, 65061.0, -2.5320256974315485, -44.24520462891361, 42738.0, -12.897090191243207, -38.33828105133945)) 14.588125378504454 15.24 List(1, 14, List(), List(8000.0, 491.49, 1.52993442E9, 19.99, 136.91, 150.0, 31.0, 35.0, 30411.0, -19.921914973916515, -43.95831084234526, 4265.0, -23.58974171521244, -46.614703714855146)) 16.86919057104893 13.67 List(1, 14, List(), List(48552.0, 60.39, 1.512073661E9, 159.9, 173.57, 8200.0, 35.0, 35.0, 13256.0, -23.012171079607057, -46.85425029097554, 2066.0, -23.50546246073055, -46.606927982370635)) 19.330008466639658 22.13 List(1, 14, List(), List(561.0, 1462.03, 1.513046106E9, 189.9, 212.03, 450.0, 35.0, 29.0, 3734.0, -23.510657419931878, -46.52425462101101, 42738.0, -12.897090191243207, -38.33828105133945)) 16.041148163712496 15.79 List(1, 14, List(), List(2160.0, 875.04, 1.518722043E9, 18.0, 33.79, 200.0, 35.0, 53.0, 8330.0, -23.619876903975946, -46.4641611021409, 71825.0, -15.886620476289508, -48.01443185354944)) 15.517755233169328 15.1 List(1, 14, List(), List(896.0, 778.14, 1.504131156E9, 7.49, 22.59, 200.0, 41.0, 35.0, 85880.0, -25.1

In [89]:
# Select (prediction, true label) and compute test error
evaluator = RegressionEvaluator(
    labelCol="freight_value", predictionCol="prediction", metricName="rmse")
rmse = evaluator.evaluate(predictions)
print("Root Mean Squared Error (RMSE) on test data = %g" % rmse)

evaluator = RegressionEvaluator(
    labelCol="freight_value", predictionCol="prediction", metricName="mae")
mae = evaluator.evaluate(predictions)
print("MAE = %g" % mae)

evaluator = RegressionEvaluator(
    labelCol="freight_value", predictionCol="prediction", metricName="r2")
r2 = evaluator.evaluate(predictions)
print("R2 = %g" % r2)

maeGLR_Gau_teste  = mae
rmseGLR_Gau_teste = rmse
r2GLR_Gau_teste   = r2

#Base cheia
#----------------------------------------------------------------------------

# Select (prediction, true label) and compute test error
evaluator = RegressionEvaluator(
    labelCol="freight_value", predictionCol="prediction", metricName="rmse")
rmse = evaluator.evaluate(predictions_Tot)
print("Root Mean Squared Error (RMSE) on test data = %g" % rmse)

evaluator = RegressionEvaluator(
    labelCol="freight_value", predictionCol="prediction", metricName="mae")
mae = evaluator.evaluate(predictions_Tot)
print("MAE = %g" % mae)

evaluator = RegressionEvaluator(
    labelCol="freight_value", predictionCol="prediction", metricName="r2")
r2 = evaluator.evaluate(predictions_Tot)
print("R2 = %g" % r2)

maeGLR_Gau_teste_Tot  = mae
rmseGLR_Gau_teste_Tot = rmse
r2GLR_Gau_teste_Tot   = r2



Root Mean Squared Error (RMSE) on test data = 3.03975
MAE = 2.30688
R2 = 0.557595
Root Mean Squared Error (RMSE) on test data = 9.86609
MAE = 5.26721
R2 = 0.619897

In [91]:
columns = ("MODELO", "MAE", "MAE_FULL", "RMSE", "RMSE_FULL", "R2", "R2_FULL")
data    = ( ('LinearRegression'                   , maeLR_teste     , maeLR_teste_Tot     , rmseLR_teste      , rmseLR_teste_Tot      , r2LR_teste       * 100,   r2LR_teste_Tot       * 100),
           ('DecisionTreeRegressor'               , maeAR_teste     , maeAR_teste_Tot     , rmseAR_teste      , rmseAR_teste_Tot      , r2AR_teste       * 100,   r2AR_teste_Tot       * 100),
           ('GBTRegressor'                        , maeGBT_teste    , maeGBT_teste_Tot    , rmseGBT_teste     , rmseGBT_teste_Tot     , r2GBT_teste      * 100,   r2GBT_teste_Tot      * 100),
           ('RandomForestRegressor'               , maeRFR_teste    , maeRFR_teste_Tot    , rmseRFR_teste     , rmseRFR_teste_Tot     , r2RFR_teste      * 100,   r2RFR_teste_Tot      * 100),
           ('GeneralizedLinearRegression Gaussian', maeGLR_Gau_teste, maeGLR_Gau_teste_Tot, rmseGLR_Gau_teste , rmseGLR_Gau_teste_Tot , r2GLR_Gau_teste  * 100,   r2GLR_Gau_teste_Tot  * 100))

rdd = spark.sparkContext.parallelize(data)
dfFromRDD1 = rdd.toDF()
dfFromRDD1 = rdd.toDF(columns)

display(dfFromRDD1.orderBy('R2', ascending=False, ))

MODELO MAE MAE_FULL RMSE RMSE_FULL R2 R2_FULL GBTRegressor 1.6829742177602103 4.473540942479851 2.434614975890428 9.219827125176893 71.62057516443838 66.80620295232022 RandomForestRegressor 1.8997635232778034 4.865857056867012 2.5946979492735562 9.919719460971242 67.76581988618263 61.57532892387621 DecisionTreeRegressor 1.90685251941861 5.050109013400841 2.652784875178676 10.186470369642779 66.30642631065373 59.48098951685474 LinearRegression 2.301002436385273 5.293480047119417 3.032605165346057 9.862082979772966 55.94360716156693 62.003370347318906 GeneralizedLinearRegression Gaussian 2.3068815598471657 5.267211130719013 3.0397542524028918 9.866085169380018 55.75950674222789 61.98971737533314

In [92]:
'''
MODELO	                                        MAE	             MAE_FULL	           RMSE	             RMSE_FULL	          R2	             R2_FULL
GBTRegressor	                        1.6829742177602103	4.473540942479851	2.434614975890428	9.219827125176893	71.62057516443838	66.80620295232022
RandomForestRegressor	                1.8997635232778034	4.865857056867012	2.5946979492735562	9.919719460971242	67.76581988618263	61.57532892387621
DecisionTreeRegressor	                1.90685251941861	5.050109013400841	2.652784875178676	10.186470369642779	66.30642631065373	59.48098951685474
LinearRegression	                    2.301002436385273	5.293480047119417	3.032605165346057	9.862082979772966	55.94360716156693	62.003370347318906
GeneralizedLinearRegression Gaussian	2.3068815598471657	5.267211130719013	3.0397542524028918	9.866085169380018	55.75950674222789	61.98971737533314

'''

Out[85]: '\nMODELO\t MAE\t MAE_FULL\t RMSE\t RMSE_FULL\t R2\t R2_FULL\nGBTRegressor\t 1.6829742177602103\t4.473540942479851\t2.434614975890428\t9.219827125176893\t71.62057516443838\t66.80620295232022\nRandomForestRegressor\t 1.8997635232778034\t4.865857056867012\t2.5946979492735562\t9.919719460971242\t67.76581988618263\t61.57532892387621\nDecisionTreeRegressor\t 1.90685251941861\t5.050109013400841\t2.652784875178676\t10.186470369642779\t66.30642631065373\t59.48098951685474\nLinearRegression\t 2.301002436385273\t5.293480047119417\t3.032605165346057\t9.862082979772966\t55.94360716156693\t62.003370347318906\nGeneralizedLinearRegression Gaussian\t2.3068815598471657\t5.267211130719013\t3.0397542524028918\t9.866085169380018\t55.75950674222789\t61.98971737533314\n\n'

In [93]:
#Sendo assim, incluo a feature product_category_name_Index para comparação dos resultados deste modelo em especifico, por se tratar do melhor modelo utilizado nesta analise
df = data_merge.select('product_category_name',
                       'distancia_sellers_customers',                     
                       'volume',               
                       'order_delivered_carrier_date',
                       'price', 
                       'payment_value',                
                       'product_weight_g', 
                       'codigo_UF_customers',
                       'codigo_UF_sellers',
                       'customer_zip_code_prefix',
                       'geolocation_lat_customer',
                       'geolocation_lng_customer',
                       'seller_zip_code_prefix',
                       'geolocation_lat_seller',
                       'geolocation_lng_seller',
                       'freight_value'
              )  

df = df.repartition(2).cache()
df.count()

from pyspark.ml.feature import StringIndexer, OneHotEncoder
from pyspark.ml.feature import VectorAssembler
#para utilização do campo no modelo de regressao, faço uma tratativa nesta feature pois a mesma esta em formato string, sendo que o modelo exige variaveis numericas
indexer = StringIndexer().setInputCol("product_category_name").setOutputCol("product_category_name_Index").fit(df)
df = indexer.transform(df)

df = df.select('product_category_name_Index',
               'volume',               
               'order_delivered_carrier_date',
               'price', 
               'payment_value',                
               'product_weight_g', 
               'codigo_UF_customers',
               'codigo_UF_sellers',
               'customer_zip_code_prefix',
               'geolocation_lat_customer',
               'geolocation_lng_customer',
               'seller_zip_code_prefix',
               'geolocation_lat_seller',
               'geolocation_lng_seller',
               'freight_value'
              )  


df = df.repartition(2).cache()
df.count()


Out[86]: 114457

In [94]:
data_merge_total = df

data_merge_total = data_merge_total.repartition(2).cache()
data_merge_total.count()

data_merge_Slice = data_merge_total.where((data_merge_total['freight_value'] > nMin) & (data_merge_total['freight_value'] < nMax))

data_merge_Slice = data_merge_Slice.repartition(2).cache()
data_merge_Slice.count()

#Antes verifico a quantidade registros que serão descartados
print(data_merge_total.count() - data_merge_Slice.count())

df = data_merge_Slice

18252

Entendendo que mesmo utilizando apenas os dados até o 3-Quartil, ainda possuo o mesmo numero de categorias de produto na base

In [96]:
df1 = (data_merge_total.select('*').groupBy('product_category_name_Index').count())
df1 = (df1.orderBy('count', ascending=False))
display(df1.select('*').limit(20))


product_category_name_Index count 0.0 11622 1.0 9731 2.0 8714 3.0 8534 4.0 7876 5.0 7154 6.0 6039 7.0 4570 8.0 4452 9.0 4273 10.0 4150 11.0 3860 12.0 3462 13.0 3103 14.0 2712 15.0 2549 16.0 2098 17.0 1983 18.0 1747 19.0 1621

In [97]:
dfC1  = (df1.select('*').groupBy('product_category_name_Index').count())
print(dfC1.select('count').count())

74

In [98]:
df2 =(data_merge_Slice.select('*').where((data_merge_Slice['freight_value'] > 1) & (data_merge_Slice['freight_value'] < 34.13)).groupBy('product_category_name_Index').count())
df2 = (df2.orderBy('count', ascending=False))
display(df2.select('*').limit(20))

product_category_name_Index count 0.0 10330 1.0 8466 2.0 7534 3.0 6906 4.0 6771 5.0 5947 6.0 5289 7.0 4285 10.0 3625 9.0 3449 8.0 3295 12.0 3225 11.0 3158 13.0 2493 14.0 2466 15.0 2183 16.0 1964 17.0 1677 19.0 1455 21.0 1014

In [99]:
#Verificamos que fazem parte desta base, os mesmas categorias de produto da base total.
dfC2  = (df2.select('*').groupBy('product_category_name_Index').count())
print(dfC2.select('count').count())

74

In [100]:
assemblerGBT = VectorAssembler(inputCols = df.columns[:-1], outputCol = 'features')
assemblerGBT_tot = VectorAssembler(inputCols = data_merge_total.columns[:-1], outputCol = 'features')

assemblerGBT = assemblerGBT.transform(df)
assemblerGBT_Tot = assemblerGBT_tot.transform(data_merge_total)
#display(assemblerGBT)

In [101]:
treinoGBT, testeGBT = assemblerGBT .randomSplit([0.7, 0.3], seed=36)
treinoGBT_Tot, testeGBT_Tot = assemblerGBT_Tot .randomSplit([0.7, 0.3], seed=36)

treinoGBT = treinoGBT.repartition(2).cache()
treinoGBT.count()

testeGBT = testeGBT.repartition(2).cache()
testeGBT.count()

treinoGBT_Tot = treinoGBT_Tot.repartition(2).cache()
treinoGBT_Tot.count()

testeGBT_Tot = testeGBT_Tot.repartition(2).cache()
testeGBT_Tot.count()

Out[93]: 34235

Após a inclusão da feature Product_Category_Name, faremos outra analise utilizando o modelo que melhor performou.

In [103]:
#GRADIENTE BOOST TREE REGRESSION

featureIndexerGBT =\
    VectorIndexer(inputCol="features", outputCol="indexedFeatures", maxCategories=100).fit(assemblerGBT)

featureIndexerGBT_Tot =\
    VectorIndexer(inputCol="features", outputCol="indexedFeatures", maxCategories=100).fit(assemblerGBT_Tot)

# Train a GBT model.
#Setada a variavel maxBins para 74, pois possuimos 74 categorias de produto e o GBTR aceita por padrao 32
gbtPCN = GBTRegressor(featuresCol="indexedFeatures", labelCol="freight_value",  maxIter=10, maxBins=74)

# Chain indexer and GBT in a Pipeline
pipelineGBT = Pipeline(stages=[featureIndexerGBT, gbtPCN])
pipelineGBT_Tot = Pipeline(stages=[featureIndexerGBT_Tot, gbtPCN])

# Train model.  This also runs the indexer.
modelgbtPCA = pipelineGBT.fit(treinoGBT)
modelgbtPCA_Tot = pipelineGBT_Tot.fit(treinoGBT_Tot)

predictionsGBT = modelgbtPCA.transform(testeGBT)
predictionsGBT_Tot = modelgbtPCA.transform(testeGBT_Tot)

predictionsGBT.select("prediction", "freight_value", "features").show(5)

# Select (prediction, true label) and compute test error
evaluator = RegressionEvaluator(
    labelCol="freight_value", predictionCol="prediction", metricName="mae")
mae = evaluator.evaluate(predictionsGBT)
print("MAE = %g" % mae)

evaluator = RegressionEvaluator(
    labelCol="freight_value", predictionCol="prediction", metricName="rmse")
rmse = evaluator.evaluate(predictionsGBT)
print("Root Mean Squared Error (RMSE) on test data = %g" % rmse)

evaluator = RegressionEvaluator(
    labelCol="freight_value", predictionCol="prediction", metricName="r2")
r2 = evaluator.evaluate(predictionsGBT)
print("R2 = %g" % r2)

maeGBT_PCA_teste  = mae
rmseGBT_PCA_teste = rmse
r2GBT_PCA_teste   = r2

gbtModel = modelgbtPCA.stages[1]
print(gbtModel)  # summary only

#Base cheia
#----------------------------------------------------------------------------

evaluator = RegressionEvaluator(
    labelCol="freight_value", predictionCol="prediction", metricName="mae")
mae = evaluator.evaluate(predictionsGBT_Tot)
print("MAE = %g" % mae)

evaluator = RegressionEvaluator(
    labelCol="freight_value", predictionCol="prediction", metricName="rmse")
rmse = evaluator.evaluate(predictionsGBT_Tot)
print("Root Mean Squared Error (RMSE) on test data = %g" % rmse)

evaluator = RegressionEvaluator(
    labelCol="freight_value", predictionCol="prediction", metricName="r2")
r2 = evaluator.evaluate(predictionsGBT_Tot)
print("R2 = %g" % r2)

maeGBT_PCA_teste_Tot  = mae
rmseGBT_PCA_teste_Tot = rmse
r2GBT_PCA_teste_Tot   = r2

+------------------+-------------+--------------------+
 prediction|freight_value| features|
+------------------+-------------+--------------------+
12.998174158497758| 7.94|[1.0,3570.0,1.513...|
14.804554406369377| 15.1|[7.0,864.0,1.5160...|
15.513013742891756| 9.34|[11.0,33300.0,1.5...|
20.863054729741545| 23.63|[0.0,7616.0,1.528...|
17.221981573294403| 18.14|[0.0,12600.0,1.50...|
+------------------+-------------+--------------------+
only showing top 5 rows

MAE = 1.73722
Root Mean Squared Error (RMSE) on test data = 2.56063
R2 = 0.686525
GBTRegressionModel (uid=GBTRegressor_f5fd112212ae) with 10 trees
MAE = 5.41968
Root Mean Squared Error (RMSE) on test data = 14.2351
R2 = 0.168054

In [104]:
columns = ("MODELO", "MAE", "MAE_FULL", "RMSE", "RMSE_FULL", "R2", "R2_FULL")
data    = (('GBTRegressor'                        , maeGBT_teste    , maeGBT_teste_Tot    , rmseGBT_teste     , rmseGBT_teste_Tot     , r2GBT_teste      * 100,   r2GBT_teste_Tot      * 100),
           ('GBTRegressor Product_Category_Name'  , maeGBT_PCA_teste, maeGBT_PCA_teste_Tot, rmseGBT_PCA_teste , rmseGBT_PCA_teste_Tot , r2GBT_PCA_teste  * 100,  r2GBT_PCA_teste_Tot  * 100))


rdd2 = spark.sparkContext.parallelize(data)
dfFromRDD2 = rdd2.toDF()
dfFromRDD2 = rdd2.toDF(columns)

display(dfFromRDD2.orderBy('R2', ascending=False ))

MODELO MAE MAE_FULL RMSE RMSE_FULL R2 R2_FULL GBTRegressor 1.6829742177602103 4.473540942479851 2.434614975890428 9.219827125176893 71.62057516443838 66.80620295232022 GBTRegressor Product_Category_Name 1.737223408500116 5.419682592124251 2.5606264366004683 14.23506543295993 68.65254958422193 16.805421774143237

In [105]:
'''
MODELO	                                   MAE	             MAE_FULL	           RMSE	             RMSE_FULL	          R2	             R2_FULL						
GBTRegressor	                    1.6829742177602103	4.473540942479851	2.434614975890428	9.219827125176893	71.62057516443838	66.80620295232022
GBTRegressor Product_Category_Name	1.737223408500116	5.419682592124251	2.5606264366004683	14.23506543295993	68.65254958422193	16.805421774143237
'''


Out[96]: '\nMODELO\t MAE\t MAE_FULL\t RMSE\t RMSE_FULL\t R2\t R2_FULL\t\t\t\t\t\t\nGBTRegressor\t 1.6829742177602103\t4.473540942479851\t2.434614975890428\t9.219827125176893\t71.62057516443838\t66.80620295232022\nGBTRegressor Product_Category_Name\t1.737223408500116\t5.419682592124251\t2.5606264366004683\t14.23506543295993\t68.65254958422193\t16.805421774143237\n'

Reparamos que o novo modelo GBTRegressor com a feature Product_Category_Name, nao performou melhor, levando tambem em consideração a metrica R2 FULL(Compoe a base com os outiliers).

FIM DO NOTEBOOK